# Airline delays 
## Bureau of Transportation Statistics
https://www.transtats.bts.gov/DL_SelectFields.asp?Table_ID=236   
https://www.bts.gov/topics/airlines-and-airports/understanding-reporting-causes-flight-delays-and-cancellations

2015 - 2019

### Additional sources
This might be useful in matching station codes to airports:
1. http://dss.ucar.edu/datasets/ds353.4/inventories/station-list.html
2. https://www.world-airport-codes.com/

In [0]:
from pyspark.sql import functions as f
from pyspark.sql.types import StructType, StructField, StringType, DoubleType, IntegerType, NullType, ShortType, DateType, BooleanType, BinaryType
from pyspark.sql import SQLContext
from pyspark.sql.functions import concat, col, hour, minute, lpad, rpad, substring, year, month, dayofmonth, lit, to_timestamp, expr,split,explode,split
from pyspark.sql.functions import isnan, when, count, col,isnull

import numpy as np
#spark = SparkSession.builder.getOrCreate()

sqlContext = SQLContext(sc)


# Weather
https://data.nodc.noaa.gov/cgi-bin/iso?id=gov.noaa.ncdc:C00532

## EDA on weather data
As a frequent flyer, we know that flight departures (and arrivals)  often get affected by weather conditions, so it makes sense to collect and process weather data corresponding to the origin and destination airports at the time of departure and arrival respectively and build features based upon this data. A weather table  has been pre-downloaded from the National Oceanic and Atmospheric Administration repository  to S3 in the form of  parquet files (thereby enabling pushdown querying and efficient joins). The weather data is for the period Jan 2015 – December 2019.

In [0]:
# ORIGINAL WEATHER DATA
weather = spark.read.option("header", "true")\
                    .parquet(f"dbfs:/mnt/mids-w261/datasets_final_project/weather_data/*.parquet")

# Adding specific date columns I need for JOIN
weather = weather.select(year(col("DATE")).alias("YEAR"), month(col("DATE")).alias("MONTH"), dayofmonth(col("DATE")).alias("DAY_OF_MONTH"), concat(rpad(lpad(hour(col("DATE")), 2, '0'), 4, '0'), lit('-'), lpad(hour(col("DATE")), 2, '0'), lit('59')).alias('HOUR_BLOCK'), *weather)

# Filter out all weather observations that don't align between station begin and end

display(weather)

YEAR MONTH DAY_OF_MONTH HOUR_BLOCK STATION DATE SOURCE LATITUDE LONGITUDE ELEVATION NAME REPORT_TYPE CALL_SIGN QUALITY_CONTROL WND CIG VIS TMP DEW SLP AW1 GA1 GA2 GA3 GA4 GE1 GF1 KA1 KA2 MA1 MD1 MW1 MW2 OC1 OD1 OD2 REM EQD AW2 AX4 GD1 AW5 GN1 AJ1 AW3 MK1 KA4 GG3 AN1 RH1 AU5 HL1 OB1 AT8 AW7 AZ1 CH1 RH3 GK1 IB1 AX1 CT1 AK1 CN2 OE1 MW5 AO1 KA3 AA3 CR1 CF2 KB2 GM1 AT5 AY2 MW6 MG1 AH6 AU2 GD2 AW4 MF1 AA1 AH2 AH3 OE3 AT6 AL2 AL3 AX5 IB2 AI3 CV3 WA1 GH1 KF1 CU2 CT3 SA1 AU1 KD2 AI5 GO1 GD3 CG3 AI1 AL1 AW6 MW4 AX6 CV1 ME1 KC2 CN1 UA1 GD5 UG2 AT3 AT4 GJ1 MV1 GA5 CT2 CG2 ED1 AE1 CO1 KE1 KB1 AI4 MW3 KG2 AA2 AX2 AY1 RH2 OE2 CU3 MH1 AM1 AU4 GA6 KG1 AU3 AT7 KD1 GL1 IA1 GG2 OD3 UG1 CB1 AI6 CI1 CV2 AZ2 AD1 AH1 WD1 AA4 KC1 IA2 CF3 AI2 AT1 GD4 AX3 AH4 KB3 CU1 CN4 AT2 CG1 CF1 GG1 MV2 CW1 GG4 AB1 AH5 CN3 2016 1 1 0000-0059 7650099999 2016-01-01T00:00:00.000+0000 4 43.435555 5.213611 22.55 PROVENCE, FR FM-12 99999 V020 190,1,N,0015,1 99999,9,9,N 007000,1,9,9 +0101,1 +0090,1 10255,1 99,9,+02250,1,99,9 9,AGL ,+99999,+99999 08,99,1,99,9,99,9,02250,1,99,9,99,9 99999,9,10216,1 8,1,004,1,+999,9 61,1 3,99,0026,1,999 SYN09807650 04857 81903 10101 20090 30216 40255 58004 69901 761// 333 4/000 69907 90710 91105 555 69905= 9999,1,9,999999,9,9 03,0000,2,1 06,0000,2,1 2016 1 1 0000-0059 7650099999 2016-01-01T00:00:00.000+0000 4 43.435555 5.213611 22.55 PROVENCE, FR FM-15 99999 V020 190,1,N,0015,1 22000,1,9,N 009000,1,9,9 +0100,1 +0090,1 99999,9 61,1 00,99,1,99,9,99,9,99999,9,99,9,99,9 10250,1,99999,9 MET057METAR LFML 010000Z AUTO 19003KT 9000 -RA NSC 10/09 Q1025= 2016 1 1 0000-0059 7650099999 2016-01-01T00:30:00.000+0000 4 43.435555 5.213611 22.55 PROVENCE, FR FM-15 99999 V020 250,1,N,0010,1 99999,9,9,N 008000,1,9,9 +9999,9 +9999,9 99999,9 10250,1,99999,9 MET056METAR LFML 010030Z AUTO 25002KT 8000 ///TCU 10/09 Q1025= Q019 2ATOD 2016 1 1 0100-0159 7650099999 2016-01-01T01:00:00.000+0000 4 43.435555 5.213611 22.55 PROVENCE, FR FM-12 99999 V020 999,9,C,0000,1 99999,9,9,N 004900,1,9,9 +0099,1 +0094,1 10251,1 99,9,+02250,1,99,9 9,AGL ,+99999,+99999 08,99,1,99,9,99,9,02250,1,99,9,99,9 99999,9,10212,1 8,1,006,1,+999,9 10,1 3,99,0015,1,999 SYN07607650 24849 80000 10099 20094 30212 40251 58006 710// 333 69925 90710 91103= 01,0002,3,1 2016 1 1 0100-0159 7650099999 2016-01-01T01:00:00.000+0000 4 43.435555 5.213611 22.55 PROVENCE, FR FM-15 99999 V020 999,9,C,0000,1 22000,1,9,N 007000,1,9,9 +0100,1 +0090,1 99999,9 00,99,1,99,9,99,9,99999,9,99,9,99,9 10250,1,99999,9 MET053METAR LFML 010100Z AUTO 00000KT 7000 NSC 10/09 Q1025= 2016 1 1 0100-0159 7650099999 2016-01-01T01:30:00.000+0000 4 43.435555 5.213611 22.55 PROVENCE, FR FM-15 99999 V020 999,9,C,0000,1 22000,1,9,N 009000,1,9,9 +0100,1 +0090,1 99999,9 00,99,1,99,9,99,9,99999,9,99,9,99,9 10250,1,99999,9 MET053METAR LFML 010130Z AUTO 00000KT 9000 NSC 10/09 Q1025= 2016 1 1 0200-0259 7650099999 2016-01-01T02:00:00.000+0000 4 43.435555 5.213611 22.55 PROVENCE, FR FM-12 99999 V020 999,9,C,0000,1 99999,9,9,N 011000,1,9,9 +0100,1 +0088,1 10254,1 99,9,+01750,1,99,9 9,AGL ,+99999,+99999 08,99,1,99,9,99,9,01750,1,99,9,99,9 99999,9,10215,1 5,1,005,1,+999,9 00,1 3,99,0010,1,999 SYN07607650 24761 80000 10100 20088 30215 40254 55005 700// 333 60005 90710 91102= 01,0000,9,1 2016 1 1 0200-0259 7650099999 2016-01-01T02:00:00.000+0000 4 43.435555 5.213611 22.55 PROVENCE, FR FM-15 99999 V020 999,9,C,0000,1 99999,9,9,Y 999999,9,9,9 +0100,1 +0090,1 99999,9 10250,1,99999,9 MET050METAR LFML 010200Z AUTO 00000KT CAVOK 10/09 Q1025= 2016 1 1 0200-0259 7650099999 2016-01-01T02:30:00.000+0000 4 43.435555 5.213611 22.55 PROVENCE, FR FM-15 99999 V020 320,1,N,0015,1 22000,1,9,N 008000,1,9,9 +0100,1 +0090,1 99999,9 00,99,1,99,9,99,9,99999,9,99,9,99,9 10250,1,99999,9 MET053METAR LFML 010230Z AUTO 32003KT 8000 NSC 10/09 Q1025= 2016 1 1 0300-0359 7650099999 2016-01-01T03:00:00.000+0000 4 43.435555 5.213611 22.55 PROVENCE, FR FM-12 99999 V020 040,1,N,0010,1 01500,1,9,N 006000,1,9,9 +0099,1 +0093,1 10253,1 07,1,+01500,1,06,1 9,AGL ,+99999,+99999 07,99,1,07,1,99,

In [0]:
weather.groupby('YEAR').count().display()

YEAR count 2015 117057365 2017 127044487 2016 126167653 2018 127793669 2019 132841262

In [0]:
#stations is a csv file that contains the details of all the weather stations and the associated 'lat' and longitude
stations = spark.read.option("header", "true").csv("dbfs:/mnt/mids-w261/DEMO8/gsod/stations.csv.gz")

cleaned_weather = weather.join(stations, [concat(col("usaf"), col("wban")) == weather.STATION, col('country') == "US"]).filter(weather.DATE.between(to_timestamp(stations.begin, 'yyyyMMdd'), to_timestamp(stations.end, 'yyyyMMdd') + expr("INTERVAL 24 hours"))).select(*weather,stations.country)

cleaned_weather.display()

YEAR MONTH DAY_OF_MONTH HOUR_BLOCK STATION DATE SOURCE LATITUDE LONGITUDE ELEVATION NAME REPORT_TYPE CALL_SIGN QUALITY_CONTROL WND CIG VIS TMP DEW SLP AW1 GA1 GA2 GA3 GA4 GE1 GF1 KA1 KA2 MA1 MD1 MW1 MW2 OC1 OD1 OD2 REM EQD AW2 AX4 GD1 AW5 GN1 AJ1 AW3 MK1 KA4 GG3 AN1 RH1 AU5 HL1 OB1 AT8 AW7 AZ1 CH1 RH3 GK1 IB1 AX1 CT1 AK1 CN2 OE1 MW5 AO1 KA3 AA3 CR1 CF2 KB2 GM1 AT5 AY2 MW6 MG1 AH6 AU2 GD2 AW4 MF1 AA1 AH2 AH3 OE3 AT6 AL2 AL3 AX5 IB2 AI3 CV3 WA1 GH1 KF1 CU2 CT3 SA1 AU1 KD2 AI5 GO1 GD3 CG3 AI1 AL1 AW6 MW4 AX6 CV1 ME1 KC2 CN1 UA1 GD5 UG2 AT3 AT4 GJ1 MV1 GA5 CT2 CG2 ED1 AE1 CO1 KE1 KB1 AI4 MW3 KG2 AA2 AX2 AY1 RH2 OE2 CU3 MH1 AM1 AU4 GA6 KG1 AU3 AT7 KD1 GL1 IA1 GG2 OD3 UG1 CB1 AI6 CI1 CV2 AZ2 AD1 AH1 WD1 AA4 KC1 IA2 CF3 AI2 AT1 GD4 AX3 AH4 KB3 CU1 CN4 AT2 CG1 CF1 GG1 MV2 CW1 GG4 AB1 AH5 CN3 country 2016 1 1 0000-0059 70305226652 2016-01-01T00:13:00.000+0000 4 61.53639 -160.34139 16.8 KALSKAG AIRPORT, AK US FM-16 99999 V020 230,1,N,0036,1 00091,1,9,N 999999,9,9,9 +0000,1 -0010,1 99999,9 9,AGL ,+99999,+99999 99,99,9,99,9,99,9,00152,1,99,9,99,9 MET079SPECI PALG 010013Z AUTO 23007KT OVC005 00/M01 RMK AO2 PWINO TSNO CIG 003V009 $= 4,99,1,+00152,1,1 US 2016 1 1 0000-0059 70305226652 2016-01-01T00:27:00.000+0000 4 61.53639 -160.34139 16.8 KALSKAG AIRPORT, AK US FM-16 99999 V020 999,9,V,0026,1 00122,1,9,N 999999,9,9,9 +0000,1 -0010,1 99999,9 9,AGL ,+99999,+99999 99,99,9,99,9,99,9,00213,1,99,9,99,9 MET079SPECI PALG 010027Z AUTO VRB05KT OVC007 00/M01 RMK AO2 PWINO TSNO CIG 004V009 $= 4,99,1,+00213,1,1 US 2016 1 1 0000-0059 70305226652 2016-01-01T00:56:00.000+0000 4 61.53639 -160.34139 16.8 KALSKAG AIRPORT, AK US FM-15 99999 V020 220,1,N,0036,1 00183,1,9,N 999999,9,9,9 +0000,1 -0005,1 99999,9 9,AGL ,+99999,+99999 99,99,9,99,9,99,9,00274,1,99,9,99,9 MET102METAR PALG 010056Z AUTO 22007KT BKN009 OVC014 00/M01 RMK AO2 PWINO TSNO T00001005 CIG 006V013 SLPNO $= 3,99,1,+00274,1,1 4,99,1,+00427,1,9 US 2016 1 1 0100-0159 70305226652 2016-01-01T01:19:00.000+0000 4 61.53639 -160.34139 16.8 KALSKAG AIRPORT, AK US FM-16 99999 V020 230,1,N,0021,1 00274,1,9,N 999999,9,9,9 +0010,1 -0010,1 99999,9 9,AGL ,+99999,+99999 99,99,9,99,9,99,9,00335,1,99,9,99,9 MET079SPECI PALG 010119Z AUTO 23004KT OVC011 01/M01 RMK AO2 PWINO TSNO CIG 009V014 $= 4,99,1,+00335,1,1 US 2016 1 1 0100-0159 70305226652 2016-01-01T01:56:00.000+0000 4 61.53639 -160.34139 16.8 KALSKAG AIRPORT, AK US FM-15 99999 V020 210,1,N,0015,1 00427,1,9,N 999999,9,9,9 +0005,1 -0011,1 99999,9 9,AGL ,+99999,+99999 99,99,9,99,9,99,9,00274,1,99,9,99,9 MET097METAR PALG 010156Z AUTO 21003KT FEW009 BKN014 OVC023 01/M01 RMK AO2 PWINO TSNO T00051011 SLPNO $= 1,99,1,+00274,1,9 3,99,1,+00427,1,9 4,99,1,+00701,1,9 US 2016 1 1 0200-0259 70305226652 2016-01-01T02:08:00.000+0000 4 61.53639 -160.34139 16.8 KALSKAG AIRPORT, AK US FM-16 99999 V020 999,9,C,0000,1 00610,1,9,N 999999,9,9,9 +0010,1 -0010,1 99999,9 9,AGL ,+99999,+99999 99,99,9,99,9,99,9,00427,1,99,9,99,9 MET081SPECI PALG 010208Z AUTO 00000KT FEW014 BKN020 OVC026 01/M01 RMK AO2 PWINO TSNO $= 1,99,1,+00427,1,9 3,99,1,+00610,1,9 4,99,1,+00792,1,9 US 2016 1 1 0200-0259 70305226652 2016-01-01T02:56:00.000+0000 4 61.53639 -160.34139 16.8 KALSKAG AIRPORT, AK US FM-15 99999 V020 110,1,N,0015,1 00549,1,9,N 999999,9,9,9 +0000,1 -0005,1 99999,9 9,AGL ,+99999,+99999 99,99,9,99,9,99,9,00091,1,99,9,99,9 MET113METAR PALG 010256Z AUTO 11003KT FEW003 BKN018 OVC025 00/M01 RMK AO2 PWINO TSNO 5//// T00001005 BKN V SCT SLPNO $= 1,99,1,+00091,1,9 3,99,1,+00549,1,9 4,99,1,+00762,1,9 US 2016 1 1 0300-0359 70305226652 2016-01-01T03:56:00.000+0000 4 61.53639 -160.34139 16.8 KALSKAG AIRPORT, AK US FM-15 99999 V020 999,9,V,0015,1 00853,1,9,N 999999,9,9,9 +0005,1 -0011,1 99999,9 9,AGL ,+99999,+99999 99,99,9,99,9,99,9,00853,1,99,9,99,9 MET083METAR PALG 010356Z AUTO VRB03KT OVC028 01/M01 RMK AO2 PWINO TSNO T00051011 SLPNO $= 4,99,1,+00853,1,9 US 2016 1 1 0400-0459 70305226652 2016-01-01T04:56:00.000+0000 4 61.53639 -160.34139 16.8 KALSKAG AIRPORT, AK US FM-15 99999 V020 999,9,V,0021,1 00945,1,

In [0]:
# we'll remove the rows from 2019 in this dataframe and treat 2019 separately as our test data
cleaned_weather = cleaned_weather.filter(cleaned_weather["YEAR"]!=2019)

In [0]:
cleaned_weather[['YEAR']].distinct().show()

+----+
YEAR|
+----+
2016|
2015|
2018|
2017|
+----+

In [0]:
weather.registerTempTable('weather')
stations.registerTempTable('stations')

cleaned_weather_19 = spark.sql("""
SELECT weather.*, stations.country
FROM weather, stations
WHERE weather.YEAR==2019 and concat(stations.usaf, stations.wban) == weather.STATION AND stations.country == 'US' """)
display(cleaned_weather_19)
cleaned_weather_19.count()

YEAR MONTH DAY_OF_MONTH HOUR_BLOCK STATION DATE SOURCE LATITUDE LONGITUDE ELEVATION NAME REPORT_TYPE CALL_SIGN QUALITY_CONTROL WND CIG VIS TMP DEW SLP AW1 GA1 GA2 GA3 GA4 GE1 GF1 KA1 KA2 MA1 MD1 MW1 MW2 OC1 OD1 OD2 REM EQD AW2 AX4 GD1 AW5 GN1 AJ1 AW3 MK1 KA4 GG3 AN1 RH1 AU5 HL1 OB1 AT8 AW7 AZ1 CH1 RH3 GK1 IB1 AX1 CT1 AK1 CN2 OE1 MW5 AO1 KA3 AA3 CR1 CF2 KB2 GM1 AT5 AY2 MW6 MG1 AH6 AU2 GD2 AW4 MF1 AA1 AH2 AH3 OE3 AT6 AL2 AL3 AX5 IB2 AI3 CV3 WA1 GH1 KF1 CU2 CT3 SA1 AU1 KD2 AI5 GO1 GD3 CG3 AI1 AL1 AW6 MW4 AX6 CV1 ME1 KC2 CN1 UA1 GD5 UG2 AT3 AT4 GJ1 MV1 GA5 CT2 CG2 ED1 AE1 CO1 KE1 KB1 AI4 MW3 KG2 AA2 AX2 AY1 RH2 OE2 CU3 MH1 AM1 AU4 GA6 KG1 AU3 AT7 KD1 GL1 IA1 GG2 OD3 UG1 CB1 AI6 CI1 CV2 AZ2 AD1 AH1 WD1 AA4 KC1 IA2 CF3 AI2 AT1 GD4 AX3 AH4 KB3 CU1 CN4 AT2 CG1 CF1 GG1 MV2 CW1 GG4 AB1 AH5 CN3 country 2019 1 1 0000-0059 99999994081 2019-01-01T00:00:00.000+0000 null 45.516 -103.3017 878.7 BUFFALO 13 ESE, SD US CRN05 99999 V020 999,9,R,0027,1 99999,9,9,N 999999,9,9,9 -0152,1 +9999,9 99999,9 010,M,-0147,1 010,N,-0154,1 060,0050,1,0,999,9,0,00100,1,0,99999,9,0 05,-0153,1,0,0670,1,0 -0152,1,0 -0135,1,0,-0160,1,0,00,1,0 05,0000,9,1 02622,1,0 0819,1,0 01,0000,9,1 -0152,1,0,0003,1,0 -0153,1,0,9999,9,0,-0147,1,0,9999,9,0 00000,1,0,00000,1,0,00000,1,0,00000,1,0 -0151,1 +9999,9,0,0002,1,0 -0152,1,0 +01986,1,0 -0154,1,0,9999,9,0,-0147,1,0,9999,9,0 0129,1,0,0125,1,0,0116,1,0 -0152,1,0 +01989,1,0 99,-07 +9999,9,0,0002,1,0 05,+00000,1,0 -0155,1,0,-0148,1,0,00002,1,0,00018,1,0 -0154,1,0,9999,9,0,-0147,1,0,9999,9,0 0792,1,0 +9999,9,0,0002,1,0 +01980,1,0 0813,1,0 11660,1,0,29130,1,0 014998,1,0,197360,1,0 US 2019 1 1 0000-0059 99999994081 2019-01-01T00:05:00.000+0000 null 45.516 -103.3017 878.7 BUFFALO 13 ESE, SD US CRN05 99999 V020 999,9,9,9999,9 99999,9,9,N 999999,9,9,9 -0153,1 +9999,9 99999,9 05,-0153,1,0,0669,1,0 -0153,1,0 05,0000,9,1 -0152,1,0 +01986,1,0 -0153,1,0 +01989,1,0 99,-07 05,+00000,1,0 +01980,1,0 11650,1,0,29130,1,0 US 2019 1 1 0000-0059 99999994081 2019-01-01T00:10:00.000+0000 null 45.516 -103.3017 878.7 BUFFALO 13 ESE, SD US CRN05 99999 V020 999,9,9,9999,9 99999,9,9,N 999999,9,9,9 -0153,1 +9999,9 99999,9 05,-0154,1,0,0674,1,0 -0153,1,0 05,0000,9,1 -0153,1,0 +01986,1,0 -0153,1,0 +01989,1,0 99,-07 05,+00000,1,0 +01979,1,0 11650,1,0,29120,1,0 US 2019 1 1 0000-0059 99999994081 2019-01-01T00:15:00.000+0000 null 45.516 -103.3017 878.7 BUFFALO 13 ESE, SD US CRN05 99999 V020 999,9,9,9999,9 99999,9,9,N 999999,9,9,9 -0154,1 +9999,9 99999,9 05,-0154,1,0,0674,1,0 -0154,1,0 05,0000,9,1 -0153,1,0 +01986,1,0 -0154,1,0 +01989,1,0 99,-07 05,+00000,1,0 +01979,1,0 11640,1,0,29120,1,0 US 2019 1 1 0000-0059 99999994081 2019-01-01T00:20:00.000+0000 null 45.516 -103.3017 878.7 BUFFALO 13 ESE, SD US CRN05 99999 V020 999,9,9,9999,9 99999,9,9,N 999999,9,9,9 -0154,1 +9999,9 99999,9 05,-0155,1,0,0671,1,0 -0154,1,0 05,0000,9,1 -0154,1,0 +01986,1,0 -0155,1,0 +01989,1,0 99,-07 05,+00000,1,0 +01979,1,0 00360,1,0,29110,1,0 US 2019 1 1 0000-0059 99999994081 2019-01-01T00:25:00.000+0000 null 45.516 -103.3017 878.7 BUFFALO 13 ESE, SD US CRN05 99999 V020 999,9,9,9999,9 99999,9,9,N 999999,9,9,9 -0155,1 +9999,9 99999,9 05,-0156,1,0,0669,1,0 -0155,1,0 05,0000,9,1 -0154,1,0 +01986,1,0 -0155,1,0 +01989,1,0 99,-07 05,+00000,1,0 +01979,1,0 00452,1,0,29120,1,0 US 2019 1 1 0000-0059 99999994081 2019-01-01T00:30:00.000+0000 null 45.516 -103.3017 878.7 BUFFALO 13 ESE, SD US CRN05 99999 V020 999,9,9,9999,9 99999,9,9,N 999999,9,9,9 -0155,1 +9999,9 99999,9 05,-0156,1,0,0669,1,0 -0155,1,0 05,0000,9,1 -0154,1,0 +01986,1,0 -0155,1,0 +01989,1,0 99,-07 05,+00000,1,0 +01979,1,0 11630,1,0,29120,1,0 US 2019 1 1 0000-0059 99999994081 2019-01-01T00:35:00.000+0000 null 45.516 -103.3017 878.7 BUFFALO 13 ESE, SD US CRN05 99999 V020 999,9,9,9999,9 99999,9,9,N 999999,9,9,9 -0156,1 +9999,9 99999,9 05,-0157,1,0,0675,1,0 -0156,1,0 05,0000,9,1 -0155,1,0 +01986,1,0 -0156,1,0 +01989,1,0 99,-07 05,+00000,1,0 +01979,1,0 11620,1,0,29120,1,0 US 2019 1 1 0000-0059 99999994081 2019-01-01T00:40:00.000+0000 null 45.5

Out[16]: 58380273

In [0]:
# The  original weather table has around 230 M records
cleaned_weather.count()

Weather plays a crucial component in scheduling and on-time prediction of the flights.In this section we analyze the data collected at various stations and would try to identify their pattern and distribution.

Goal - We have the following high-level goals in mind:
- Understand the distribution of various variables.
- Understand the pattern with a goal to identify outliers and possible errors in reading(s).

Data :
Weather data is collected from various weather sensors placed at different stations. Each station has a corresponding number and readings from that station.
Let us start by taking an overall statistical summary of the data.

## Preface
The Integrated Surface Dataset (ISD) is composed of worldwide surface weather observations from over 35,000 stations parameters included are: air quality, atmospheric pressure, atmospheric temperature/dew point, atmospheric winds, clouds, precipitation, ocean waves, tides and more. 

We can broadly classify the elements of the dataset into two main categories:
- Mandatory data =>The mandatory data section contains meteorological information on the basic elements such as winds, visibility, and temperature.
These are the most commonly reported parameters and are available most of the time.
- Additional Data Section => These additional data contain information of significance and/or which are received with varying degrees of frequency.

For the purpose of this study :
- We will limit the weather observations to the stations in the US only.
- We'll focus on mandatory data section as the additional data is missing for most of the records.
- We'll ignore the 'remarks section as ,as these are a set of characeters in plain language that do not provide much insight into decision making.

### Analysis of Mandatory data variables.

#### W1.0-Station
This field represents a unique station id and is formed from the concatenation of weather station id and WBAN id. We'll use this identifier to get the weather details at a particular location.

#### W2.0 - Date
This field indicates a timestamp when the reading was taken corresponding to a station.

#### W3.0 Source 
This is categorical data attribute.The flag of a GEOPHYSICAL-POINT-OBSERVATION showing the source or combination of sources used in creating the
observation.
We analyze the distribution of this column below.

### W4.0 Latitude and Longitude information.
This is latitude and longitude co-ordinate of a geo-location.

###W5.0 Report- type
The code that denotes the type of geophysical surface observation.

### W6.0 Elevation
The elevation of a GEOPHYSICAL-POINT-OBSERVATION relative to Mean Sea Level (MSL).

### W7.0 Call_sign
 The identifier that represents the call letters assigned to a FIXED-WEATHER-STATION.
   - Missing values are denoted by 99999

#### W8.0 Quality Control 
 The name of the quality control process applied to a weather observation.
   - V01 = No A or M Quality Control applied
   - V02 = Automated Quality Control
   - V03 = subjected to Quality Control

### Weather observations- readings from various weather stations
The section below describes the actuel readings that are made from the sensors.

#### W9.0 Wind
The wind measurement is a composite field in our observation and consists of the following attributes.

#### W9.1 WIND-OBSERVATION direction angle
The angle(in angular degrees), measured in a clockwise direction, between true north and the direction from which the wind is blowing.

### W9.2 WIND-OBSERVATION direction quality code
The code that denotes a quality status of a reported WIND-OBSERVATION direction angle.
 0 = Passed gross limits check
 1 = Passed all quality control checks
 2 = Suspect
 3 = Erroneous
 4 = Passed gross limits check, data originate from an NCEI data source
 5 = Passed all quality control checks, data originate from an NCEI data source
 6 = Suspect, data originate from an NCEI data source
 7 = Erroneous, data originate from an NCEI data source
 9 = Passed gross limits check if element is present
 
#### W9.2 Filters
   - We'll not use the following values in our analysis:
     - 2 = Suspect
     - 3 = Erroneous
     
### W9.3 WIND-OBSERVATION type code
The code that denotes the character of the WIND-OBSERVATION.


### W9.4 WIND-OBSERVATION speed rate
 The rate of horizontal travel of air past a fixed point.

**NOTE: If a value of 9 appears with a wind speed of 0000, this indicates calm winds.

### W9.5 WIND-OBSERVATION speed quality code
 The code that denotes a quality status of a reported WIND-OBSERVATION speed rate.
- 0 = Passed gross limits check
- 1 = Passed all quality control checks
- 2 = Suspect
- 3 = Erroneous
- 4 = Passed gross limits check, data originate from an NCEI data source
- 5 = Passed all quality control checks, data originate from an NCEI data source
- 6 = Suspect, data originate from an NCEI data source
- 7 = Erroneous, data originate from an NCEI data source
- 9 = Passed gross limits check if element is present
 
#### W9.5 WIND-OBSERVATION speed quality code filters
We'll only retain the observations with the following values in our analysis
- 0 = Passed gross limits check
- 1 = Passed all quality control checks
- 4 = Passed gross limits check, data originate from an NCEI data source
- 5 = Passed all quality control checks, data originate from an NCEI data source
- 9 = Passed gross limits check if element is present

### 10.Sky condition observations
The section below describes the high level description of the sky-condition observations.

### W10.1 SKY-CONDITION-OBSERVATION ceiling height dimension
The height above ground level (AGL) of the lowest cloud or obscuring phenomena layer aloft with 5/8 or more summation total sky
cover, which may be predominantly opaque, or the vertical visibility into a surface-based obstruction.

### W10.2 SKY-CONDTION-OBSERVATION ceiling quality code
 The code that denotes a quality status of a reported ceiling height dimension.
 - 0 = Passed gross limits check
 - 1 = Passed all quality control checks
 - 2 = Suspect
 - 3 = Erroneous
 - 4 = Passed gross limits check, data originate from an NCEI data source
 - 5 = Passed all quality control checks, data originate from an NCEI data source
 - 6 = Suspect, data originate from an NCEI data source
 - 7 = Erroneous, data originate from an NCEI data source
 - 9 = Passed gross limits check if element is present
 
#### W10.2 SKY-CONDTION-OBSERVATION ceiling quality code filters
 - 0 = Passed gross limits check
 - 1 = Passed all quality control checks
 - 4 = Passed gross limits check, data originate from an NCEI data source
 - 5 = Passed all quality control checks, data originate from an NCEI data source
 - 9 = Passed gross limits check if element is present
 
### W10.3 SKY-CONDTION-OBSERVATION ceiling quality code
The code that denotes the method used to determine the ceiling.
 - A = Aircraft
 - B = Balloon
 - C = Statistically derived
 - D = Persistent cirriform ceiling (pre-1950 data)
 - E = Estimated
 - M = Measured
 - P = Precipitation ceiling (pre-1950 data)
 - R = Radar
 - S = ASOS augmented
 - U = Unknown ceiling (pre-1950 data)
 - V = Variable ceiling (pre-1950 data)
 - W = Obscured
 - 9 = Missing

#### W10.3 SKY-CONDTION-OBSERVATION ceiling quality code filter
We'll only use the following attributes in our analysis.
 - A = Aircraft
 - B = Balloon
 - C = Statistically derived
 - E = Estimated
 - M = Measured
 - R = Radar
 - S = ASOS augmented
 - W = Obscured
 
 

### W10.4 SKY-CONDITION-OBSERVATION CAVOK code
 The code that represents whether the 'Ceiling and Visibility Okay' (CAVOK) condition has been reported.
- N = No
- Y = Yes
- 9 = Missing

#### W10.4 SKY-CONDITION-OBSERVATION CAVOK code filter
We'll only use the following in our analysis:
- N= No
- Y = Yes

### Visibility observations
The section below provides a brief overview of the explanatory variables that indicate visibility

### W11.1 VISIBILITY-OBSERVATION distance dimension
The horizontal distance at which an object can be seen and identified.

### W11.2 VISIBILITY-OBSERVATION distance quality code
The horizontal distance at which an object can be seen and identified.
The code that denotes a quality status of a reported distance of a visibility observation.
 - 0 = Passed gross limits check
 - 1 = Passed all quality control checks
 - 4 = Passed gross limits check, data originate from an NCEI data source
 - 5 = Passed all quality control checks, data originate from an NCEI data source
 - 6 = Suspect, data originate from an NCEI data source
 - 7 = Erroneous, data originate from an NCEI data source
 - 9 = Passed gross limits check if element is present

#### W11.1 VISIBILITY-OBSERVATION distance quality code filter
We'll only retain the observations with the following attributes 
 - 0 = Passed gross limits check
 - 1 = Passed all quality control checks
 - 4 = Passed gross limits check, data originate from an NCEI data source
 - 5 = Passed all quality control checks, data originate from an NCEI data source
 - 9 = Passed gross limits check if element is present


### W11.3  VISIBILITY-OBSERVATION variability code
The code that denotes whether or not the reported visibility is variable.
 - N = Not variable
 - V = Variable
 - 9 = Missing

### W11.4 VISIBILITY-OBSERVATION quality variability code
The code that denotes a quality status of a reported VISIBILITY-OBSERVATION variability code.
 - 0 = Passed gross limits check
 - 1 = Passed all quality control checks
 - 2 = Suspect
 - 3 = Erroneous
 - 4 = Passed gross limits check, data originate from an NCEI data source
 - 5 = Passed all quality control checks, data originate from an NCEI data source
 - 6 = Suspect, data originate from an NCEI data source
 - 7 = Erroneous, data originate from an NCEI data source
 - 9 = Passed gross limits check if element is present

#### W11.4  VISIBILITY-OBSERVATION quality variability code filter
We'll only retain the following values in our analysis:
 - 0 = Passed gross limits check
 - 1 = Passed all quality control checks
 - 4 = Passed gross limits check, data originate from an NCEI data source
 - 5 = Passed all quality control checks, data originate from an NCEI data source
 - 9 = Passed gross limits check if element is present

### Air Temperature attributes.
The section below provides a geenral overview of the data attributes for the observations on air temperature.

### W12.1 Air temperature
 The temperature of the air.
 MIN: -0932 MAX: +0618 UNITS: Degrees Celsius
 SCALING FACTOR: 10
### W12.1 Air Temperature filter
Missing values are indicated by +9999 and will be ignored

### W12.2 Air temperature quality code
 The code that denotes a quality status of an AIR-TEMPERATURE-OBSERVATION.
   - 0 = Passed gross limits check
   - 1 = Passed all quality control checks
   - 2 = Suspect
   - 3 = Erroneous
   - 4 = Passed gross limits check, data originate from an NCEI data source
   - 5 = Passed all quality control checks, data originate from an NCEI data source
   - 6 = Suspect, data originate from an NCEI data source
   - 7 = Erroneous, data originate from an NCEI data source
   - 9 = Passed gross limits check if element is present
   - A = Data value flagged as suspect, but accepted as a good value
   - C = Temperature and dew point received from Automated Weather Observing System (AWOS) 
   - I = Data value not originally in data, but inserted by validator
   - M = Manual changes made to value based on information provided by NWS or FAA
   - P = Data value not originally flagged as suspect, but replaced by validator
   - R = Data value replaced with value computed by NCEI software
   - U = Data value replaced with edited value 
#### W12.2 Air temperature quality code filter
We'll only retain the following values
   - 0 = Passed gross limits check
   - 1 = Passed all quality control checks
   - 4 = Passed gross limits check, data originate from an NCEI data source
   - 5 = Passed all quality control checks, data originate from an NCEI data source
   - 9 = Passed gross limits check if element is present
   - A = Data value flagged as suspect, but accepted as a good value
   - C = Temperature and dew point received from Automated Weather Observing System (AWOS) 
   - I = Data value not originally in data, but inserted by validator
   - M = Manual changes made to value based on information provided by NWS or FAA
   - P = Data value not originally flagged as suspect, but replaced by validator
   - R = Data value replaced with value computed by NCEI software
   - U = Data value replaced with edited value

### Dew Point observations
The sectio below describes the key attributes of the dew-point data collected from weather stations.

### W13.1 Dew Point temperature
The temperature in ,Degrees Celsius,to which a given parcel of air must be cooled at constant pressure and water vapor content in order for saturation to occur.
MIN: -0982 MAX: +0368 UNITS: 

### W13.2 Dew point quality code
 The code that denotes a quality status of the reported dew point temperature.
 - 0 = Passed gross limits check
 - 1 = Passed all quality control checks
 - 2 = Suspect
 - 3 = Erroneous
 - 4 = Passed gross limits check, data originate from an NCEI data source
 - 5 = Passed all quality control checks, data originate from an NCEI data source
 - 6 = Suspect, data originate from an NCEI data source
 - 7 = Erroneous, data originate from an NCEI data source
 - 9 = Passed gross limits check if element is present
 - A = Data value flagged as suspect, but accepted as a good value
 - C = Temperature and dew point received from Automated Weather Observing System (AWOS) 
 - I = Data value not originally in data, but inserted by validator
 - M = Manual changes made to value based on information provided by NWS or FAA
 - P = Data value not originally flagged as suspect, but replaced by validator
 - R = Data value replaced with value computed by NCEI software
 - U = Data value replaced with edited value
#### W13.2 Dew point quality code filter
 We'll retain the following values for our analysis
 - 0 = Passed gross limits check
 - 1 = Passed all quality control checks
 - 4 = Passed gross limits check, data originate from an NCEI data source
 - 5 = Passed all quality control checks, data originate from an NCEI data source
 - 9 = Passed gross limits check if element is present
 - A = Data value flagged as suspect, but accepted as a good value
 - C = Temperature and dew point received from Automated Weather Observing System (AWOS) 
 - I = Data value not originally in data, but inserted by validator
 - M = Manual changes made to value based on information provided by NWS or FAA
 - P = Data value not originally flagged as suspect, but replaced by validator
 - R = Data value replaced with value computed by NCEI software
 - U = Data value replaced with edited value

### Atmospheric Pressure
The section below describes the various data observations on atmospheric pressure.

#### W14.1 Sea level pressure 
The air pressure relative to Mean Sea Level (MSL).
#### W14.1 Sea level pressure filter
Missing values are denoted by 99999 and wo;; be ignored

#### W14.1 Sea level pressure quality code
 The code that denotes a quality status of the sea level pressure of an observation
 - 0 = Passed gross limits check
 - 1 = Passed all quality control checks
 - 2 = Suspect
 - 3 = Erroneous
 - 4 = Passed gross limits check, data originate from an NCEI data source
 - 5 = Passed all quality control checks, data originate from an NCEI data source
 - 6 = Suspect, data originate from an NCEI data source
 - 7 = Erroneous, data originate from an NCEI data sou
 - 9 = Passed gross limits check if element is present
 
#### W14.2 Sea level pressure quality code filter
 We'll only retain the following observations.
 - 0 = Passed gross limits check
 - 1 = Passed all quality control checks
 - 4 = Passed gross limits check, data originate from an NCEI data source
 - 5 = Passed all quality control checks, data originate from an NCEI data source
 - 9 = Passed gross limits check if element is present

### Additional Data section
As mentioned in the section above the 'additional data' corresponds to the attributes which are observed in addition to the mandatory observations. We present our analysis below on this additional data.

In [0]:
all_cols = cleaned_weather.columns

  
  

In [0]:

# df.orderBy(["age","city"],ascending=[0,1]).collect()
#[cleaned_weather.groupBy("AW1").count().orderBy(["count","AW1"],ascending = False).collect()][0]

In [0]:
# vals = []
# for col in (range(20,len(all_cols))):
#   print(cleaned_weather[col])
#   vals.append(cleaned_weather.groupBy(cleaned_weather[col]).count().orderBy(["count",cleaned_weather[col]],ascending = False).take(1))
#   #print(vals.append(cleaned_weather.groupBy(cleaned_weather[col]).count().orderBy(["count",cleaned_weather[col]],ascending = False).take(1)))


In [0]:
# for i in vals:
#   print(f'\n {i}')
  
  

### Dropping columns with NA values
As we have seen in the previous section the columns that represent 'Additional Data' in the weather table has a lot of NA values. 
We'll remove these columns and work with the columns that indicate 'Mandatory weather variables'

In [0]:
cols_list = cleaned_weather.columns

In [0]:
# getting an index of all the columns
for i in range(0,len(cols_list)):
  print(f'i = {i} and col = {cols_list[i]}')
  
  

i = 0 and col = YEAR
i = 1 and col = MONTH
i = 2 and col = DAY_OF_MONTH
i = 3 and col = HOUR_BLOCK
i = 4 and col = STATION
i = 5 and col = DATE
i = 6 and col = SOURCE
i = 7 and col = LATITUDE
i = 8 and col = LONGITUDE
i = 9 and col = ELEVATION
i = 10 and col = NAME
i = 11 and col = REPORT_TYPE
i = 12 and col = CALL_SIGN
i = 13 and col = QUALITY_CONTROL
i = 14 and col = WND
i = 15 and col = CIG
i = 16 and col = VIS
i = 17 and col = TMP
i = 18 and col = DEW
i = 19 and col = SLP
i = 20 and col = AW1
i = 21 and col = GA1
i = 22 and col = GA2
i = 23 and col = GA3
i = 24 and col = GA4
i = 25 and col = GE1
i = 26 and col = GF1
i = 27 and col = KA1
i = 28 and col = KA2
i = 29 and col = MA1
i = 30 and col = MD1
i = 31 and col = MW1
i = 32 and col = MW2
i = 33 and col = OC1
i = 34 and col = OD1
i = 35 and col = OD2
i = 36 and col = REM
i = 37 and col = EQD
i = 38 and col = AW2
i = 39 and col = AX4
i = 40 and col = GD1
i = 41 and col = AW5
i = 42 and col = GN1
i = 43 and col = AJ1
i = 44 and col = AW3
i = 45 and col = MK1
i = 46 and col = KA4
i = 47 and col = GG3
i = 48 and col = AN1
i = 49 and col = RH1
i = 50 and col = AU5
i = 51 and col = HL1
i = 52 and col = OB1
i = 53 and col = AT8
i = 54 and col = AW7
i = 55 and col = AZ1
i = 56 and col = CH1
i = 57 and col = RH3
i = 58 and col = GK1
i = 59 and col = IB1
i = 60 and col = AX1
i = 61 and col = CT1
i = 62 and col = AK1
i = 63 and col = CN2
i = 64 and col = OE1
i = 65 and col = MW5
i = 66 and col = AO1
i = 67 and col = KA3
i = 68 and col = AA3
i = 69 and col = CR1
i = 70 and col = CF2
i = 71 and col = KB2
i = 72 and col = GM1
i = 73 and col = AT5
i = 74 and col = AY2
i = 75 and col = MW6
i = 76 and col = MG1
i = 77 and col = AH6
i = 78 and col = AU2
i = 79 and col = GD2
i = 80 and col = AW4
i = 81 and col = MF1
i = 82 and col = AA1
i = 83 and col = AH2
i = 84 and col = AH3
i = 85 and col = OE3
i = 86 and col = AT6
i = 87 and col = AL2
i = 88 and col = AL3
i = 89 and col = AX5
i = 90 and col = IB2
i = 91 and col = AI3
i = 92 and col = CV3
i = 93 and col = WA1
i = 94 and col = GH1
i = 95 and col = KF1
i = 96 and col = CU2
i = 97 and col = CT3
i = 98 and col = SA1
i = 99 and col = AU1
i = 100 and col = KD2
i = 101 and col = AI5
i = 102 and col = GO1
i = 103 and col = GD3
i = 104 and col = CG3
i = 105 and col = AI1
i = 106 and col = AL1
i = 107 and col = AW6
i = 108 and col = MW4
i = 109 and col = AX6
i = 110 and col = CV1
i = 111 and col = ME1
i = 112 and col = KC2
i = 113 and col = CN1
i = 114 and col = UA1
i = 115 and col = GD5
i = 116 and col = UG2
i = 117 and col = AT3
i = 118 and col = AT4
i = 119 and col = GJ1
i = 120 and col = MV1
i = 121 and col = GA5
i = 122 and col = CT2
i = 123 and col = CG2
i = 124 and col = ED1
i = 125 and col = AE1
i = 126 and col = CO1
i = 127 and col = KE1
i = 128 and col = KB1
i = 129 and col = AI4
i = 130 and col = MW3
i = 131 and col = KG2
i = 132 and col = AA2
i = 133 and col = AX2
i = 134 and col = AY1
i = 135 and col = RH2
i = 136 and col = OE2
i = 137 and col = CU3
i = 138 and col = MH1
i = 139 and col = AM1
i = 140 and col = AU4
i = 141 and col = GA6
i = 142 and col = KG1
i = 143 and col = AU3
i = 144 and col = AT7
i = 145 and col = KD1
i = 146 and col = GL1
i = 147 and col = IA1
i = 148 and col = GG2
i = 149 and col = OD3
i = 150 and col = UG1
i = 151 and col = CB1
i = 152 and col = AI6
i = 153 and col = CI1
i = 154 and col = CV2
i = 155 and col = AZ2
i = 156 and col = AD1
i = 157 and col = AH1
i = 158 and col = WD1
i = 159 and col = AA4
i = 160 and col = KC1
i = 161 and col = IA2
i = 162 and col = CF3
i = 163 and col = AI2
i = 164 and col = AT1
i = 165 and col = GD4
i = 166 and col = AX3
i = 167 and col = AH4
i = 168 and col = KB3
i = 169 and col = CU1
i = 170 and col = CN4
i = 171 and col = AT2
i = 172 and col = CG1
i = 173 and col = CF1
i = 174 and col = GG1
i = 175 and col = MV2
i = 176 and col = CW1
i = 177 and col = GG4
i = 178 and col = AB1
i = 179 and col = AH5
i = 180 and col = CN3
i = 181 and col = country

In [0]:
# Now lets drop the columns
temp_df = cleaned_weather
temp_df_new = cleaned_weather

cleaned_weather_trimmed = cleaned_weather

for i in range(20,len(cols_list)):
  print(f'ith column = {cols_list[i]}')
  temp_df_new = temp_df.drop(cols_list[i])
  cleaned_weather_trimmed = temp_df_new 
  temp_df = temp_df_new
  
#clean_weather_trimmed = temp_df_new
  
  
  
  

ith column = AW1
ith column = GA1
ith column = GA2
ith column = GA3
ith column = GA4
ith column = GE1
ith column = GF1
ith column = KA1
ith column = KA2
ith column = MA1
ith column = MD1
ith column = MW1
ith column = MW2
ith column = OC1
ith column = OD1
ith column = OD2
ith column = REM
ith column = EQD
ith column = AW2
ith column = AX4
ith column = GD1
ith column = AW5
ith column = GN1
ith column = AJ1
ith column = AW3
ith column = MK1
ith column = KA4
ith column = GG3
ith column = AN1
ith column = RH1
ith column = AU5
ith column = HL1
ith column = OB1
ith column = AT8
ith column = AW7
ith column = AZ1
ith column = CH1
ith column = RH3
ith column = GK1
ith column = IB1
ith column = AX1
ith column = CT1
ith column = AK1
ith column = CN2
ith column = OE1
ith column = MW5
ith column = AO1
ith column = KA3
ith column = AA3
ith column = CR1
ith column = CF2
ith column = KB2
ith column = GM1
ith column = AT5
ith column = AY2
ith column = MW6
ith column = MG1
ith column = AH6
ith column = AU2
ith column = GD2
ith column = AW4
ith column = MF1
ith column = AA1
ith column = AH2
ith column = AH3
ith column = OE3
ith column = AT6
ith column = AL2
ith column = AL3
ith column = AX5
ith column = IB2
ith column = AI3
ith column = CV3
ith column = WA1
ith column = GH1
ith column = KF1
ith column = CU2
ith column = CT3
ith column = SA1
ith column = AU1
ith column = KD2
ith column = AI5
ith column = GO1
ith column = GD3
ith column = CG3
ith column = AI1
ith column = AL1
ith column = AW6
ith column = MW4
ith column = AX6
ith column = CV1
ith column = ME1
ith column = KC2
ith column = CN1
ith column = UA1
ith column = GD5
ith column = UG2
ith column = AT3
ith column = AT4
ith column = GJ1
ith column = MV1
ith column = GA5
ith column = CT2
ith column = CG2
ith column = ED1
ith column = AE1
ith column = CO1
ith column = KE1
ith column = KB1
ith column = AI4
ith column = MW3
ith column = KG2
ith column = AA2
ith column = AX2
ith column = AY1
ith column = RH2
ith column = OE2
ith column = CU3
ith column = MH1
ith column = AM1
ith column = AU4
ith column = GA6
ith column = KG1
ith column = AU3
ith column = AT7
ith column = KD1
ith column = GL1
ith column = IA1
ith column = GG2
ith column = OD3
ith column = UG1
ith column = CB1
ith column = AI6
ith column = CI1
ith column = CV2
ith column = AZ2
ith column = AD1
ith column = AH1
ith column = WD1
ith column = AA4
ith column = KC1
ith column = IA2
ith column = CF3
ith column = AI2
ith column = AT1
ith column = GD4
ith column = AX3
ith column = AH4
ith column = KB3
ith column = CU1
ith column = CN4
ith column = AT2
ith column = CG1
ith column = CF1
ith column = GG1
ith column = MV2
ith column = CW1
ith column = GG4
ith column = AB1
ith column = AH5
ith column = CN3
ith column = country

### Column split
Now that we've removed the unwanted columns we will focus on individual weather attibutes(WND etc.).
These observations related to the weather are grouped in a single column and we want to split it into multiple columns.

In the section that follows , we aim to wplit each combined column into multiple ones to continue our analysis.

#### Split 1- The Wind attributes.
The wind column has been combined to indicate the following attribute values of the measurement related to the wind:
- W1=>WIND-OBSERVATION direction angle,the angle, measured in a clockwise direction, between true north and the direction from which the wind is blowing.
 MIN: 001 MAX: 360 UNITS: Angular Degrees
 SCALING FACTOR: 1
 999 = Missing. If type code (below) = V, then 999 indicates variable wind direction.
 
- W2=> WIND-OBSERVATION direction quality code.The code that denotes a quality status of a reported WIND-OBSERVATION direction angle.

- W3=> WIND-OBSERVATION type code.The code that denotes the character of the WIND-OBSERVATION.
  - '9' indicates that the data is missing.

- W4=> WIND-OBSERVATION speed rate. The rate of horizontal travel of air past a fixed point.
 UNITS: meters per second
 SCALING FACTOR: 10.
 - 9999 indicates missing values
 
 - W5 =>WIND-OBSERVATION speed quality code. The code that denotes a quality status of a reported WIND-OBSERVATION speed rate.
 
 We'll now create additional columns in our "trimmed_data_frame" to represent these values as separate columns.
 
 - WND_Angle = WIND-OBSERVATION direction angle
 - WND_Qlty = WIND-OBSERVATION direction quality code
 - WND_Obs = WIND-OBSERVATION type code
 - WND_Speed = WIND-OBSERVATION speed rate
 - WND_Speed_Qlty = WIND-OBSERVATION speed quality code

In [0]:
#Let us now try to append these columns to the data frame
#df_concat = df_1.union(df_2)
from functools import reduce



#clean_weather_trimmed_split = clean_weather_trimmed.union(df_split)

In [0]:
# The code below splits the comma separated column values into individual columns.
#- WND_Angle = WIND-OBSERVATION direction angle
 #- WND_Qlty = WIND-OBSERVATION direction quality code
 #- WND_Obs = WIND-OBSERVATION type code
 #- WND_Speed = WIND-OBSERVATION speed rate
 #- WND_Speed_Qlty = WIND-OBSERVATION speed quality code
#weather_split = weather_split.withColumn('WIND_DIR', split_col.getItem(0).cast(IntegerType()))

split_col = f.split(cleaned_weather['WND'], ',')
cleaned_weather = cleaned_weather.withColumn('WND_Angle', split_col.getItem(0).cast(IntegerType()))
cleaned_weather = cleaned_weather.withColumn('WND_Qlty', split_col.getItem(1))
cleaned_weather = cleaned_weather.withColumn('WND_Obs', split_col.getItem(2))
cleaned_weather = cleaned_weather.withColumn('WND_Speed', split_col.getItem(3).cast(IntegerType()))
cleaned_weather = cleaned_weather.withColumn('WND_Speed_Qlty', split_col.getItem(4))
#df = df.withColumn('NAME2', split_col.getItem(1))

In [0]:
split_col = f.split(cleaned_weather['WND'], ',')
cleaned_weather_19 = cleaned_weather_19.withColumn('WND_Angle', split_col.getItem(0).cast(IntegerType()))
cleaned_weather_19 = cleaned_weather_19.withColumn('WND_Qlty', split_col.getItem(1))
cleaned_weather_19 = cleaned_weather_19.withColumn('WND_Obs', split_col.getItem(2))
cleaned_weather_19 = cleaned_weather_19.withColumn('WND_Speed', split_col.getItem(3).cast(IntegerType()))
cleaned_weather_19 = cleaned_weather_19.withColumn('WND_Speed_Qlty', split_col.getItem(4))

#### Split 2- The Sky Conditions

This column provides more information about the conditions of the sky.
We'll split the data into the following columns.

In [0]:
# We'll now split the CGI obervations into muliple columns

split_col = f.split(cleaned_weather['CIG'], ',')
cleaned_weather = cleaned_weather.withColumn('CIG_Height', split_col.getItem(0).cast(IntegerType()))
cleaned_weather = cleaned_weather.withColumn('CIG_Qlty', split_col.getItem(1))
cleaned_weather = cleaned_weather.withColumn('CIG_Ceiling', split_col.getItem(2))
cleaned_weather = cleaned_weather.withColumn('CIG_CAVOK', split_col.getItem(3))

#df = df.withColumn('NAME2', split_col.getItem(1))

In [0]:
split_col = f.split(cleaned_weather['CIG'], ',')
cleaned_weather_19 = cleaned_weather_19.withColumn('CIG_Height', split_col.getItem(0).cast(IntegerType()))
cleaned_weather_19 = cleaned_weather_19.withColumn('CIG_Qlty', split_col.getItem(1))
cleaned_weather_19 = cleaned_weather_19.withColumn('CIG_Ceiling', split_col.getItem(2))
cleaned_weather_19 = cleaned_weather_19.withColumn('CIG_CAVOK', split_col.getItem(3))

#### Split 3- The Visibility Conditions

This column provides more information about the visibility conditions.

In [0]:
#We will now split the column into muliple cols

split_col = f.split(cleaned_weather['VIS'], ',')
cleaned_weather = cleaned_weather.withColumn('VIS_Dis', split_col.getItem(0).cast(IntegerType()))
cleaned_weather = cleaned_weather.withColumn('VIS_Qlty', split_col.getItem(1))
cleaned_weather = cleaned_weather.withColumn('VIS_Var', split_col.getItem(2))
cleaned_weather = cleaned_weather.withColumn('VIS_Var_Qlty', split_col.getItem(3))



In [0]:
split_col = f.split(cleaned_weather['VIS'], ',')
cleaned_weather_19 = cleaned_weather_19.withColumn('VIS_Dis', split_col.getItem(0).cast(IntegerType()))
cleaned_weather_19 = cleaned_weather_19.withColumn('VIS_Qlty', split_col.getItem(1))
cleaned_weather_19 = cleaned_weather_19.withColumn('VIS_Var', split_col.getItem(2))
cleaned_weather_19 = cleaned_weather_19.withColumn('VIS_Var_Qlty', split_col.getItem(3))

#### Split 4- The Temperature Observations

This column provides more information about the temperature conditions.

In [0]:

split_col = f.split(cleaned_weather['TMP'], ',')
cleaned_weather = cleaned_weather.withColumn('TMP_Degree', split_col.getItem(0).cast(IntegerType()))
cleaned_weather = cleaned_weather.withColumn('TMP_Qlty', split_col.getItem(1))


In [0]:
split_col = f.split(cleaned_weather['TMP'], ',')
cleaned_weather_19 = cleaned_weather_19.withColumn('TMP_Degree', split_col.getItem(0).cast(IntegerType()))
cleaned_weather_19 = cleaned_weather_19.withColumn('TMP_Qlty', split_col.getItem(1))

#### Split 5- The Dew Observations

These attributes indicate the Dew observations of the air

In [0]:
#SPlitting the DEW column


split_col = f.split(cleaned_weather['DEW'], ',')
cleaned_weather = cleaned_weather.withColumn('DEW_Degree', split_col.getItem(0).cast(IntegerType()))
cleaned_weather = cleaned_weather.withColumn('DEW_Qlty', split_col.getItem(1))

In [0]:
split_col = f.split(cleaned_weather['DEW'], ',')
cleaned_weather_19 = cleaned_weather_19.withColumn('DEW_Degree', split_col.getItem(0).cast(IntegerType()))
cleaned_weather_19 = cleaned_weather_19.withColumn('DEW_Qlty', split_col.getItem(1))

#### Split 6- The Pressure Observations

These attributes indicate the atmospheric pressure measurements.

In [0]:
split_col = f.split(cleaned_weather['SLP'], ',')
cleaned_weather = cleaned_weather.withColumn('SLP_Pressure', split_col.getItem(0).cast(IntegerType()))
cleaned_weather = cleaned_weather.withColumn('SLP_Qlty', split_col.getItem(1))

In [0]:
split_col = f.split(cleaned_weather['SLP'], ',')
cleaned_weather_19 = cleaned_weather_19.withColumn('SLP_Pressure', split_col.getItem(0).cast(IntegerType()))
cleaned_weather_19 = cleaned_weather_19.withColumn('SLP_Qlty', split_col.getItem(1))

##### Now our dataframe has all the columns that are split into individual values.WE'll now get rid of the aggregated columns - WND, SLP,VIS and TMP.

#### Let's now get rid of the redundant columns

In [0]:
cleaned_weather_final = cleaned_weather.drop("WND","CIG","VIS","TMP","DEW","SLP")
cleaned_weather_19_final = cleaned_weather_19.drop("WND","CIG","VIS","TMP","DEW","SLP")

In [0]:
#ANalyzing the cols

for i in range(10,len(cleaned_weather_final.columns)):
  print(cleaned_weather_final[i])
  #print(cleaned_weather_final.groupBy(cleaned_weather_final[i]).count().orderBy(["count",cleaned_weather_final[i]],ascending = False))
  
        
  

#for col in (range(20,len(all_cols))):
#   print(cleaned_weather[col])
#   vals.append(cleaned_weather.groupBy(cleaned_weather[col]).count().orderBy(["count",cleaned_weather[col]],ascending = False).take(1))
#   #print(vals.append(cleaned_weather.groupBy(cleaned_weather[col]).count().orderBy(["count",cleaned_weather[col]],ascending = False).take(1)))

Column<b'NAME'>
Column<b'REPORT_TYPE'>
Column<b'CALL_SIGN'>
Column<b'QUALITY_CONTROL'>
Column<b'AW1'>
Column<b'GA1'>
Column<b'GA2'>
Column<b'GA3'>
Column<b'GA4'>
Column<b'GE1'>
Column<b'GF1'>
Column<b'KA1'>
Column<b'KA2'>
Column<b'MA1'>
Column<b'MD1'>
Column<b'MW1'>
Column<b'MW2'>
Column<b'OC1'>
Column<b'OD1'>
Column<b'OD2'>
Column<b'REM'>
Column<b'EQD'>
Column<b'AW2'>
Column<b'AX4'>
Column<b'GD1'>
Column<b'AW5'>
Column<b'GN1'>
Column<b'AJ1'>
Column<b'AW3'>
Column<b'MK1'>
Column<b'KA4'>
Column<b'GG3'>
Column<b'AN1'>
Column<b'RH1'>
Column<b'AU5'>
Column<b'HL1'>
Column<b'OB1'>
Column<b'AT8'>
Column<b'AW7'>
Column<b'AZ1'>
Column<b'CH1'>
Column<b'RH3'>
Column<b'GK1'>
Column<b'IB1'>
Column<b'AX1'>
Column<b'CT1'>
Column<b'AK1'>
Column<b'CN2'>
Column<b'OE1'>
Column<b'MW5'>
Column<b'AO1'>
Column<b'KA3'>
Column<b'AA3'>
Column<b'CR1'>
Column<b'CF2'>
Column<b'KB2'>
Column<b'GM1'>
Column<b'AT5'>
Column<b'AY2'>
Column<b'MW6'>
Column<b'MG1'>
Column<b'AH6'>
Column<b'AU2'>
Column<b'GD2'>
Column<b'AW4'>
Column<b'MF1'>
Column<b'AA1'>
Column<b'AH2'>
Column<b'AH3'>
Column<b'OE3'>
Column<b'AT6'>
Column<b'AL2'>
Column<b'AL3'>
Column<b'AX5'>
Column<b'IB2'>
Column<b'AI3'>
Column<b'CV3'>
Column<b'WA1'>
Column<b'GH1'>
Column<b'KF1'>
Column<b'CU2'>
Column<b'CT3'>
Column<b'SA1'>
Column<b'AU1'>
Column<b'KD2'>
Column<b'AI5'>
Column<b'GO1'>
Column<b'GD3'>
Column<b'CG3'>
Column<b'AI1'>
Column<b'AL1'>
Column<b'AW6'>
Column<b'MW4'>
Column<b'AX6'>
Column<b'CV1'>
Column<b'ME1'>
Column<b'KC2'>
Column<b'CN1'>
Column<b'UA1'>
Column<b'GD5'>
Column<b'UG2'>
Column<b'AT3'>
Column<b'AT4'>
Column<b'GJ1'>
Column<b'MV1'>
Column<b'GA5'>
Column<b'CT2'>
Column<b'CG2'>
Column<b'ED1'>
Column<b'AE1'>
Column<b'CO1'>
Column<b'KE1'>
Column<b'KB1'>
Column<b'AI4'>
Column<b'MW3'>
Column<b'KG2'>
Column<b'AA2'>
Column<b'AX2'>
Column<b'AY1'>
Column<b'RH2'>
Column<b'OE2'>
Column<b'CU3'>
Column<b'MH1'>
Column<b'AM1'>
Column<b'AU4'>
Column<b'GA6'>
Column<b'KG1'>
Column<b'AU3'>
Column<b'AT7'>
Column<b'KD1'>
Column<b'GL1'>
Column<b'IA1'>
Column<b'GG2'>
Column<b'OD3'>
Column<b'UG1'>
Column<b'CB1'>
Column<b'AI6'>
Column<b'CI1'>
Column<b'CV2'>
Column<b'AZ2'>
Column<b'AD1'>
Column<b'AH1'>
Column<b'WD1'>
Column<b'AA4'>
Column<b'KC1'>
Column<b'IA2'>
Column<b'CF3'>
Column<b'AI2'>
Column<b'AT1'>
Column<b'GD4'>
Column<b'AX3'>
Column<b'AH4'>
Column<b'KB3'>
Column<b'CU1'>
Column<b'CN4'>
Column<b'AT2'>
Column<b'CG1'>
Column<b'CF1'>
Column<b'GG1'>
Column<b'MV2'>
Column<b'CW1'>
Column<b'GG4'>
Column<b'AB1'>
Column<b'AH5'>
Column<b'CN3'>
Column<b'country'>
Column<b'WND_Angle'>
Column<b'WND_Qlty'>
Column<b'WND_Obs'>
Column<b'WND_Speed'>
Column<b'WND_Speed_Qlty'>
Column<b'CIG_Height'>
Column<b'CIG_Qlty'>
Column<b'CIG_Ceiling'>
Column<b'CIG_CAVOK'>
Column<b'VIS_Dis'>
Column<b'VIS_Qlty'>
Column<b'VIS_Var'>
Column<b'VIS_Var_Qlty'>
Column<b'TMP_Degree'>
Column<b'TMP_Qlty'>
Column<b'DEW_Degree'>
Column<b'DEW_Qlty'>
Column<b'SLP_Pressure'>
Column<b'SLP_Qlty'>

## Analysis of Weather Attributes.
Now that we have finalized our data frame , let's analyze the Individueal features.

#### Section 1 - Analysis of "Wind"

###### 1.1 Wind Angle -  The angle, measured in a clockwise direction, between true north and the direction from which the wind is blowing.

- Type = Quantitative
- Range = 1 - 360
- Missing  = 999

In [0]:
#Lets look at the statistics of WND_Angle
cleaned_weather_final[['WND_Angle']].describe().show()


+-------+------------------+
summary| WND_Angle|
+-------+------------------+
 count| 220310191|
 mean| 554.0002292812683|
 stddev|408.70385514151076|
 min| 1|
 max| 999|
+-------+------------------+

In [0]:
#Analysis of Missing values

WND_Angle_NA =cleaned_weather_final.filter(cleaned_weather_final["WND_Angle"] == 999)

In [0]:
WND_Angle_present =cleaned_weather_final.filter(cleaned_weather_final["WND_Angle"] != 999)

###### The plot below shows the average angle of WIND

In [0]:
WND_Angle_present[['YEAR','WND_Angle']].display()

YEAR WND_Angle 2016 230 2016 220 2016 230 2016 210 2016 110 2016 90 2016 90 2016 90 2016 100 2016 90 2016 90 2016 90 2016 100 2016 110 2016 100 2016 80 2016 90 2016 80 2016 70 2016 80 2016 60 2016 30 2016 90 2016 80 2016 70 2016 110 2016 80 2016 80 2016 20 2016 60 2016 50 2016 60 2016 70 2016 80 2016 100 2016 100 2016 90 2016 90 2016 100 2016 110 2016 90 2016 100 2016 100 2016 100 2016 100 2016 90 2016 110 2016 100 2016 100 2016 110 2016 150 2016 150 2016 160 2016 160 2016 190 2016 180 2016 130 2016 160 2016 150 2016 150 2016 110 2016 90 2016 90 2016 100 2016 90 2016 80 2016 80 2016 90 2016 90 2016 90 2016 100 2016 100 2016 100 2016 100 2016 100 2016 100 2016 100 2016 110 2016 100 2016 100 2016 100 2016 100 2016 110 2016 110 2016 100 2016 100 2016 100 2016 110 2016 100 2016 100 2016 100 2016 100 2016 90 2016 100 2016 100 2016 100 2016 110 2016 100 2016 120 2016 110 2016 100 2016 110 2016 100 2016 100 2016 110 2016 110 2016 130 2016 110 2016 120 2016 100 2016 140 2016 110 2016 110 2016 100 2016 100 2016 100 2016 100 2016 120 2016 100 2016 100 2016 100 2016 90 2016 90 2016 100 2016 90 2016 90 2016 90 2016 90 2016 100 2016 90 2016 100 2016 100 2016 90 2016 90 2016 110 2016 100 2016 70 2016 130 2016 100 2016 110 2016 100 2016 90 2016 100 2016 100 2016 90 2016 100 2016 100 2016 90 2016 90 2016 90 2016 100 2016 100 2016 90 2016 100 2016 90 2016 90 2016 100 2016 100 2016 90 2016 100 2016 110 2016 90 2016 90 2016 120 2016 70 2016 90 2016 260 2016 70 2016 260 2016 90 2016 70 2016 60 2016 330 2016 50 2016 60 2016 60 2016 50 2016 60 2016 80 2016 70 2016 80 2016 90 2016 90 2016 90 2016 100 2016 100 2016 100 2016 110 2016 110 2016 110 2016 110 2016 100 2016 110 2016 100 2016 100 2016 100 2016 90 2016 90 2016 350 2016 50 2016 60 2016 220 2016 250 2016 100 2016 90 2016 100 2016 100 2016 80 2016 90 2016 100 2016 90 2016 100 2016 90 2016 90 2016 120 2016 100 2016 90 2016 90 2016 100 2016 100 2016 120 2016 150 2016 140 2016 140 2016 140 2016 160 2016 180 2016 170 2016 180 2016 180 2016 190 2016 190 2016 200 2016 180 2016 200 2016 200 2016 190 2016 200 2016 190 2016 200 2016 190 2016 180 2016 170 2016 170 2016 150 2016 130 2016 130 2016 130 2016 90 2016 100 2016 120 2016 100 2016 110 2016 90 2016 70 2016 80 2016 70 2016 80 2016 80 2016 80 2016 70 2016 70 2016 70 2016 70 2016 70 2016 70 2016 80 2016 80 2016 80 2016 70 2016 60 2016 70 2016 60 2016 70 2016 90 2016 60 2016 80 2016 320 2016 70 2016 70 2016 70 2016 100 2016 60 2016 280 2016 60 2016 50 2016 110 2016 100 2016 90 2016 60 2016 30 2016 40 2016 60 2016 60 2016 80 2016 60 2016 70 2016 80 2016 80 2016 60 2016 80 2016 100 2016 70 2016 40 2016 70 2016 70 2016 50 2016 80 2016 80 2016 90 2016 70 2016 110 2016 120 2016 10 2016 20 2016 70 2016 10 2016 60 2016 50 2016 50 2016 50 2016 50 2016 60 2016 50 2016 50 2016 50 2016 50 2016 60 2016 50 2016 50 2016 70 2016 70 2016 50 2016 60 2016 60 2016 70 2016 70 2016 80 2016 60 2016 50 2016 50 2016 40 2016 80 2016 50 2016 40 2016 30 2016 100 2016 70 2016 30 2016 30 2016 20 2016 40 2016 20 2016 310 2016 30 2016 320 2016 290 2016 50 2016 70 2016 40 2016 60 2016 50 2016 40 2016 40 2016 40 2016 50 2016 50 2016 50 2016 50 2016 80 2016 40 2016 60 2016 70 2016 70 2016 70 2016 70 2016 90 2016 100 2016 50 2016 110 2016 100 2016 90 2016 80 2016 260 2016 130 2016 100 2016 100 2016 80 2016 90 2016 70 2016 100 2016 100 2016 90 2016 100 2016 90 2016 100 2016 90 2016 90 2016 90 2016 100 2016 100 2016 100 2016 100 2016 100 2016 80 2016 70 2016 340 2016 60 2016 60 2016 100 2016 90 2016 90 2016 90 2016 80 2016 80 2016 80 2016 90 2016 80 2016 60 2016 80 2016 90 2016 100 2016 100 2016 100 2016 100 2016 100 2016 100 2016 100 2016 100 2016 100 2016 100 2016 120 2016 90 2016 290 2016 50 2016 30 2016 40 2016 30 2016 30 2016 80 2016 80 2016 40 2016 90 2016 80 2016 90 2016 90 2016 100 2016 90 2016 100 2016 100 2016 110 2016 120 2016 90 2016 90 2016 100 2016 110 2016 100 2016 90 2016 240 2016 230 2016 240 2016 250 2016 110 2016 100 2016 110 2016 100 2016 100 2016 130 2016 110 2016 10

###### Missing values of WND_ANGLE over the years

In [0]:
WND_Angle_NA[['YEAR','WND_Angle']].display()

YEAR WND_Angle 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 999 2016 99

##### Observation:
- The number of missing values for WND_ANGLE are roughly the same each year.

In [0]:
all_cols = cleaned_weather_final.columns

#### 1.2 Wind Qlty -The code that denotes a quality status of a reported WIND-OBSERVATION direction angle.
- Type = Qualitative
- Range = 0-9
- 0 = Passed gross limits check
- 1 = Passed all quality control checks
- 2 = Suspect
- 3 = Erroneous
- 4 = Passed gross limits check, data originate from an NCEI data source
- 5 = Passed all quality control checks, data originate from an NCEI data source
- 6 = Suspect, data originate from an NCEI data source
- 7 = Erroneous, data originate from an NCEI data source
- 9 = Passed gross limits check if element is present

In [0]:
#cleaned_weather_final.groupBy(cleaned_weather_final['WND_Qlty']).count().orderBy(["count",cleaned_weather_final['WND_Qlty']],ascending = False)

cleaned_weather_final[['WND_Qlty','YEAR']].groupBy("WND_Qlty","YEAR").count().display()

WND_Qlty YEAR count 1 2018 6178703 9 2018 25513781 5 2018 25511728 9 2017 24122839 5 2017 25613925 1 2017 4116496 U 2018 125 9 2016 24621467 1 2016 3772786 5 2016 26188116 U 2016 96 1 2015 3029461 U 2015 110 9 2015 24712627 5 2015 26927664 7 2017 3 P 2017 31 P 2016 27 7 2015 5 P 2015 45 U 2017 86 A 2017 1 P 2018 58 7 2018 3 A 2016 2 A 2018 3 7 2016 1 2 2015 2

###### Observation:
Wind Quality:
-Our domain for this variable is 0-9 and  'Quality status' = 'U' , 'A' , 'P' are unknown values that we should drop.

###### 1.3 Wind_Obs- The code that denotes the character of the WIND-OBSERVATION.

Type = Qualitative
- Missing Values = 9
- A = Abridged Beaufort
- B = Beaufort
- C = Calm
- H = 5-Minute Average Speed
- N = Normal
- R = 60-Minute Average Speed
- Q = Squall
- T = 180 Minute Average Speed
- V = Variable

In [0]:
cleaned_weather_final[['WND_Obs']].groupBy("WND_Obs").count().display()

WND_Obs count V 5602149 C 33342921 N 122394772 9 60135747 R 4899686 H 3658606

##### Observation:
Wind_Obs:
-Almost 30% of the the values are unknown and should be analyzed further/dropped.

#### 1.4 Wind_Speed
- (Scaling factor = 10)
- Units = m/sec
- Type = Quantitative
- Scaling = 10
- Missing Values = 99999

In [0]:
WND_Speed_NA = cleaned_weather_final.filter(cleaned_weather_final["WND_Speed"] != 99999)

### The Bar chart below shows average Wind speed over the years

In [0]:
WND_Speed_NA[['WND_Speed','YEAR']].display()

WND_Speed YEAR 36 2016 26 2016 36 2016 21 2016 15 2016 0 2016 15 2016 15 2016 21 2016 0 2016 26 2016 31 2016 36 2016 41 2016 46 2016 51 2016 51 2016 36 2016 21 2016 0 2016 36 2016 41 2016 41 2016 51 2016 51 2016 57 2016 41 2016 62 2016 31 2016 41 2016 77 2016 36 2016 57 2016 57 2016 26 2016 36 2016 46 2016 46 2016 36 2016 31 2016 41 2016 46 2016 31 2016 36 2016 41 2016 46 2016 57 2016 62 2016 51 2016 46 2016 57 2016 67 2016 36 2016 51 2016 62 2016 62 2016 41 2016 31 2016 21 2016 41 2016 36 2016 46 2016 46 2016 31 2016 26 2016 26 2016 26 2016 26 2016 26 2016 21 2016 36 2016 31 2016 36 2016 31 2016 31 2016 41 2016 36 2016 31 2016 36 2016 46 2016 62 2016 57 2016 88 2016 57 2016 67 2016 62 2016 62 2016 57 2016 36 2016 41 2016 46 2016 46 2016 62 2016 46 2016 46 2016 57 2016 57 2016 57 2016 77 2016 67 2016 51 2016 51 2016 82 2016 67 2016 46 2016 51 2016 67 2016 36 2016 46 2016 67 2016 57 2016 57 2016 51 2016 62 2016 51 2016 57 2016 67 2016 62 2016 26 2016 46 2016 31 2016 41 2016 62 2016 67 2016 72 2016 72 2016 62 2016 51 2016 46 2016 46 2016 0 2016 0 2016 0 2016 31 2016 26 2016 31 2016 36 2016 41 2016 41 2016 41 2016 57 2016 41 2016 36 2016 57 2016 51 2016 57 2016 57 2016 41 2016 26 2016 15 2016 0 2016 0 2016 46 2016 31 2016 26 2016 46 2016 46 2016 46 2016 62 2016 46 2016 57 2016 51 2016 57 2016 51 2016 51 2016 67 2016 57 2016 57 2016 62 2016 62 2016 77 2016 67 2016 72 2016 62 2016 41 2016 36 2016 26 2016 0 2016 21 2016 26 2016 15 2016 41 2016 26 2016 31 2016 26 2016 0 2016 21 2016 21 2016 0 2016 26 2016 0 2016 46 2016 21 2016 31 2016 21 2016 0 2016 15 2016 15 2016 0 2016 36 2016 21 2016 0 2016 15 2016 0 2016 0 2016 0 2016 0 2016 26 2016 26 2016 26 2016 31 2016 41 2016 57 2016 51 2016 46 2016 46 2016 46 2016 62 2016 31 2016 0 2016 31 2016 26 2016 41 2016 57 2016 77 2016 72 2016 62 2016 67 2016 77 2016 88 2016 62 2016 57 2016 72 2016 62 2016 57 2016 46 2016 31 2016 21 2016 26 2016 15 2016 0 2016 31 2016 15 2016 0 2016 0 2016 0 2016 0 2016 0 2016 0 2016 0 2016 15 2016 15 2016 31 2016 21 2016 0 2016 0 2016 0 2016 0 2016 31 2016 0 2016 31 2016 21 2016 21 2016 15 2016 21 2016 0 2016 46 2016 41 2016 46 2016 57 2016 51 2016 51 2016 57 2016 51 2016 57 2016 46 2016 31 2016 46 2016 9999 2016 57 2016 46 2016 41 2016 31 2016 26 2016 36 2016 21 2016 41 2016 36 2016 31 2016 46 2016 51 2016 46 2016 41 2016 46 2016 51 2016 51 2016 46 2016 51 2016 57 2016 46 2016 41 2016 41 2016 51 2016 36 2016 41 2016 31 2016 36 2016 31 2016 31 2016 26 2016 0 2016 31 2016 21 2016 0 2016 15 2016 9999 2016 15 2016 21 2016 15 2016 0 2016 0 2016 0 2016 26 2016 21 2016 21 2016 21 2016 15 2016 26 2016 31 2016 21 2016 41 2016 36 2016 41 2016 36 2016 51 2016 46 2016 46 2016 57 2016 51 2016 51 2016 36 2016 51 2016 41 2016 31 2016 46 2016 62 2016 46 2016 36 2016 21 2016 57 2016 51 2016 36 2016 21 2016 36 2016 51 2016 51 2016 46 2016 36 2016 46 2016 21 2016 46 2016 51 2016 51 2016 31 2016 21 2016 36 2016 72 2016 57 2016 36 2016 21 2016 46 2016 31 2016 46 2016 31 2016 26 2016 21 2016 15 2016 26 2016 15 2016 0 2016 31 2016 41 2016 31 2016 26 2016 26 2016 41 2016 36 2016 51 2016 36 2016 41 2016 46 2016 31 2016 46 2016 41 2016 41 2016 31 2016 36 2016 36 2016 41 2016 26 2016 15 2016 9999 2016 41 2016 41 2016 21 2016 26 2016 36 2016 36 2016 46 2016 36 2016 51 2016 26 2016 26 2016 36 2016 26 2016 31 2016 0 2016 15 2016 0 2016 21 2016 0 2016 0 2016 31 2016 26 2016 31 2016 15 2016 0 2016 21 2016 15 2016 36 2016 36 2016 21 2016 31 2016 0 2016 21 2016 26 2016 15 2016 57 2016 31 2016 36 2016 31 2016 57 2016 26 2016 36 2016 46 2016 41 2016 57 2016 46 2016 62 2016 62 2016 62 2016 51 2016 51 2016 41 2016 31 2016 36 2016 31 2016 41 2016 31 2016 31 2016 21 2016 36 2016 41 2016 41 2016 41 2016 36 2016 46 2016 31 2016 31 2016 26 2016 46 2016 15 2016 31 2016 31 2016 9999 2016 31 2016 21 2016 31 2016 21 2016 26 2016 26 2016 21 2016 15 2016 26 2016 31 2016 41 2016 26 2016 21 2016 36 2016 31 2016 31 2016 26 2016 36 2016 15 2016 15 2016 31 2016 36 2016 46 2016 41 2016 15 2016 26 2016 15 2016 0 2016 

In [0]:
cleaned_weather_final[['WND_Speed']].describe().show()

In [0]:
#Analysis of missing values

WND_NA = cleaned_weather_final.filter(cleaned_weather_final["WND_Speed"] == 9999)

--------------------------------------------------------------------------- 
 NameError Traceback (most recent call last)
 <command-667068395499744> in <module> 
 1 #Analysis of missing values 
 2 
 ----> 3 WND_NA = cleaned_weather_final . filter ( cleaned_weather_final [ "WND_Speed" ] == 9999 ) 

 NameError : name 'cleaned_weather_final' is not defined

### count of Missing values for WND_SPEED over the years

In [0]:
WND_NA[['WND_Speed','YEAR']].display()

--------------------------------------------------------------------------- 
 NameError Traceback (most recent call last)
 <command-4061768275131037> in <module> 
 ----> 1 WND_NA [ [ 'WND_Speed' , 'YEAR' ] ] . display ( ) 

 NameError : name 'WND_NA' is not defined

##### Observation:
Wind_Speed:
- Almost 6M records have missing values.
- The number is same across the years.

###### 1.4 Wind_Speed_Qlty  The code that denotes a quality status of a reported WIND-OBSERVATION speed rate.

Type = Qualitative

- 0 = Passed gross limits check
- 1 = Passed all quality control checks
- 2 = Suspect
- 3 = Erroneous
- 4 = Passed gross limits check, data originate from an NCEI data source
- 5 = Passed all quality control checks, data originate from an NCEI data source
- 6 = Suspect, data originate from an NCEI data source
- 7 = Erroneous, data originate from an NCEI data source
- 9 = Passed gross limits check if element is present

In [0]:
cleaned_weather_final[['WND_Speed_Qlty','YEAR']].groupBy("WND_Speed_Qlty",'YEAR').count().display()

WND_Speed_Qlty YEAR count 9 2016 14811047 9 2019 2469988 5 2016 34050200 9 2017 14358821 9 2018 15112765 5 2017 33361515 6 2016 7491 6 2019 1091 6 2017 6667 5 2018 33243163 5 2019 6134228 6 2018 5662 2 2015 318 1 2015 4801144 6 2015 6103 9 2015 14983214 A 2015 1183 5 2015 34876238 1 2017 6122286 A 2017 1319 P 2017 1944 7 2017 335 2 2019 72 P 2019 495 U 2019 32 1 2019 1117501 A 2019 258 I 2019 2 7 2015 149 P 2015 1391 U 2015 124 1 2018 8838732 7 2018 143 A 2018 1187 P 2018 2248 2 2018 298 1 2016 5710495 A 2016 1251 I 2015 50 U 2018 147 7 2019 23 I 2018 56 U 2017 92 P 2016 1455 U 2016 108 7 2016 212 2 2017 369 I 2016 30 2 2016 206 I 2017 33

##### Observation:
Wind Speed Quality:
-Our domain for this variable is 0-9 and  'Quality status' = 'U' , 'A' , 'P' , 'I' are unknown values that we should drop.

#### Section 2 - Analysis of "SKY Conditions"

###### 2.1 CIG_Height.
The height above ground level (AGL) of the lowest cloud or obscuring phenomena layer , which may be predominantly opaque, or the vertical visibility into a surface-based obstruction.
- Type = Quantitative
- Range = 0-22000
- Missing  = 99999

In [0]:
cleaned_weather_final[['CIG_Height']].describe().show()

+-------+-----------------+
summary| CIG_Height|
+-------+-----------------+
 count| 230033881|
 mean|41859.43454373141|
 stddev|41655.03527885317|
 min| 0|
 max| 99999|
+-------+-----------------+

In [0]:
# Lets Check the number of missing values
cleaned_weather_final.filter(cleaned_weather_final["CIG_Height"] == 99999).count()

Out[43]: 75878410

In [0]:
CIG_Height_present = cleaned_weather_final.filter(cleaned_weather_final["CIG_Height"] != 99999)

### The bar chart below displays the average of lowest obscuring phenomena over the years

In [0]:
CIG_Height_present[['CIG_Height','YEAR']].display()

CIG_Height YEAR 91 2016 122 2016 183 2016 274 2016 427 2016 610 2016 549 2016 853 2016 945 2016 1067 2016 1189 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 1189 2016 22000 2016 1311 2016 1250 2016 3048 2016 2438 2016 22000 2016 3353 2016 22000 2016 1189 2016 3048 2016 2591 2016 3353 2016 3353 2016 22000 2016 1036 2016 1433 2016 1463 2016 792 2016 792 2016 1372 2016 1280 2016 1128 2016 1128 2016 1067 2016 1097 2016 1219 2016 22000 2016 914 2016 914 2016 853 2016 792 2016 3658 2016 3353 2016 3048 2016 22000 2016 22000 2016 2286 2016 792 2016 640 2016 701 2016 1128 2016 1189 2016 640 2016 945 2016 1128 2016 1067 2016 1067 2016 1250 2016 22000 2016 22000 2016 1524 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 732 2016 1219 2016 2743 2016 2743 2016 1158 2016 1189 2016 22000 2016 22000 2016 2896 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 3353 2016 22000 2016 22000 2016 2896 2016 3658 2016 823 2016 3658 2016 3353 2016 22000 2016 945 2016 701 2016 22000 2016 22000 2016 823 2016 1036 2016 762 2016 701 2016 701 2016 22000 2016 22000 2016 366 2016 1829 2016 1463 2016 22000 2016 22000 2016 22000 2016 22000 2016 2286 2016 1067 2016 1006 2016 945 2016 945 2016 3658 2016 1097 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 762 2016 22000 2016 22000 2016 792 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 3353 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 1311 2016 22000 2016 22000 2016 22000 2016 3353 2016 3658 2016 22000 2016 22000 2016 3048 2016 3048 2016 22000 2016 2743 2016 1311 2016 22000 2016 2134 2016 2591 2016 22000 2016 22000 2016 22000 2016 22000 2016 1829 2016 671 2016 1981 2016 22000 2016 22000 2016 22000 2016 1829 2016 1981 2016 1829 2016 1981 2016 2134 2016 2134 2016 1250 2016 22000 2016 1433 2016 22000 2016 1372 2016 22000 2016 1981 2016 1433 2016 1280 2016 1219 2016 22000 2016 22000 2016 2134 2016 2134 2016 22000 2016 22000 2016 2438 2016 2438 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 1829 2016 1829 2016 1524 2016 1402 2016 1250 2016 1067 2016 853 2016 610 2016 91 2016 549 2016 549 2016 792 2016 701 2016 701 2016 762 2016 914 2016 823 2016 884 2016 1676 2016 792 2016 853 2016 427 2016 823 2016 823 2016 1067 2016 1250 2016 579 2016 22000 2016 701 2016 579 2016 823 2016 22000 2016 22000 2016 22000 2016 1280 2016 22000 2016 22000 2016 22000 2016 1341 2016 22000 2016 1219 2016 1280 2016 1250 2016 1372 2016 1433 2016 1494 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 22000 2016 396 2016 22000 2016 396 2016 122 2016 457 2016 396 2016 335 2016 122 2016 122 201

###### Observation:
CIG_Height:
- We have around 75878410 records that are missing.
- The vertical visibility does not change much on an average.

###### 2.2 CIG_Qlty
The code that denotes a quality status of a reported ceiling height dimension.

- Type = Qualitative
- 0 = Passed gross limits check
- 1 = Passed all quality control checks
- 2 = Suspect
- 3 = Erroneous
- 4 = Passed gross limits check, data originate from an NCEI data source
- 5 = Passed all quality control checks, data originate from an NCEI data source
- 6 = Suspect, data originate from an NCEI data source
- 7 = Erroneous, data originate from an NCEI data source
- 9 = Passed gross limits check if element is present

In [0]:
cleaned_weather_final[['CIG_Qlty','YEAR']].groupBy("CIG_Qlty","YEAR").count().display()

CIG_Qlty YEAR count 1 2018 4311387 7 2018 107996 9 2018 19664789 5 2018 33109520 6 2018 10709 7 2015 93932 1 2015 2429997 6 2015 6103 9 2015 17644213 5 2015 34495669 9 2016 17992576 1 2016 2930682 5 2016 33542824 7 2016 110016 6 2016 6397 9 2017 17600691 5 2017 33034075 6 2017 8653 1 2017 3105975 7 2017 103987

###### Observation:
CIG_Height:
- This seems to be an important factor as the value is of 'reasonable' quality for all the records

###### 2.3 CIG_Ceiling 
 The code that denotes the method used to determine the ceiling.

- Type = Qualitative
- Missing = 9
- Measured = 'M'
- Obscures = 'W'

In [0]:
cleaned_weather_final[['CIG_Ceiling']].groupBy("CIG_Ceiling").count().display()

CIG_Ceiling count M 53676401 C 69328 W 1360256 9 165204206

##### Observation:
CIG_Ceiling:
- Almost 171M values are missing and should be dropped.

#### 2.4 CIG_CAVOK 
 The code that represents whether the 'Ceiling and Visibility Okay' (CAVOK) condition has been reported.

- Type = Qualitative
- Missing = 9

In [0]:
cleaned_weather_final[['CIG_CAVOK']].groupBy("CIG_CAVOK").count().display()

CIG_CAVOK count N 217790362 9 2519829

##### Observation:
CIG_CAVOK:
- Intesresting to note that there are no values for which CAVOK is 'Y'

#### Section 3 - Analysis of "Visibility Conditions"

###### 3.1 VIS_Dis
 The horizontal distance at which an object can be seen and identified.
- Units = Meters
- Type = Quantitative
- Range = 0-160000
- Missing  = 999999

In [0]:
# Lets take a count of missing values
cleaned_weather_final.filter(cleaned_weather_final["VIS_Dis"] == 999999).count()

Out[89]: 69770868

##### Observation:
VIS_DIS:
- 69770868 missing values

In [0]:
VIS_DIS_present = cleaned_weather_final.filter(cleaned_weather_final["VIS_DIS"] != 999999)

###### Plot- Avg Visibility over years

In [0]:
VIS_DIS_present[['VIS_DIS','YEAR']].display()

VIS_DIS YEAR 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 12875 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 6437 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 8047 2016 16093 2016 6437 2016 11265 2016 12875 2016 16093 2016 16093 2016 4023 2016 11265 2016 16093 2016 16093 2016 16093 2016 16093 2016 3219 2016 2414 2016 2012 2016 2414 2016 4828 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 9656 2016 6437 2016 8047 2016 8047 2016 9656 2016 9656 2016 8047 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016 16093 2016

#### 3.2 VIS_Qlty
 The code that denotes a quality status of a reported distance of a visibility observation.

- Type = Qualitative
- Range = 0-9
- 0 = Passed gross limits check
-  1 = Passed all quality control checks
- 2 = Suspect
- 3 = Erroneous
- 4 Passed gross limits check, data originate from an NCEI data source
- 5 = Passed all quality control checks, data originate from an NCEI data source
- 6 = Suspect, data originate from an NCEI data source-  7 = Erroneous, data originate from an NCEI data source
- 9 = Passed gross limits check if element is present

In [0]:
cleaned_weather_final[['VIS_Qlty']].groupBy("VIS_Qlty").count().display()

VIS_Qlty count 7 1096651 5 140361452 6 155321 A 59423 9 71721490 1 16619889 P 19653 I 2

##### Observation:
VIS_QLTY:
- The values 'I','P','A' are outside our domain and should be dropped

###### 3.3 VIS_Var
The code that denotes whether or not the reported visibility is variable.


- Type = Qualitative
- Range = N,V,9

In [0]:
cleaned_weather_final[['VIS_Var','YEAR']].groupBy("VIS_Var",'YEAR').count().display()

VIS_Var YEAR count 9 2016 20122624 N 2016 34284852 V 2016 175019 N 2017 33554127 N 2018 33477701 V 2017 196136 9 2017 20103118 9 2018 23546096 V 2018 180604 V 2015 182940 N 2015 35114634 9 2015 19372340

#### 3.4 VIS_Var_Qlty
- Type = Qualitative
- Range = 0-9

In [0]:
cleaned_weather_final[['VIS_Var_Qlty']].groupBy("VIS_Var_Qlty").count().show()

+------------+---------+
VIS_Var_Qlty| count|
+------------+---------+
 5|143159440|
 A| 244501|
 9| 86629940|
+------------+---------+

##### Observation:
VIS_QLTY:
- The value A' is outside our domain and should be dropped
- We shuld also further analyze the data values which are missing

#### Section 4 - Analysis of "Temperature"

###### 4.1 TMP_Degree
The temperature of the air in Degree Celcius

- Type = Quantitaive
- Scaling = 10
- Missing  =9999

In [0]:
cleaned_weather_final.filter(cleaned_weather_final["TMP_Degree"] == 9999).count()

Out[93]: 4896568

In [0]:
TMP_Degree_NA = cleaned_weather_final.filter(cleaned_weather_final["TMP_Degree"] == 9999)

###### Count of Missing values for TMP over the Years

In [0]:
TMP_Degree_NA[['TMP_Degree','YEAR']].display()

TMP_Degree YEAR 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999 2016 9999

In [0]:
TMP_Degree_Not_NA = cleaned_weather_final.filter(cleaned_weather_final["TMP_Degree"] != 9999)

###### Avg TMP over the years

In [0]:
TMP_Degree_Not_NA[['TMP_Degree','YEAR']].display()

TMP_Degree YEAR 0 2016 0 2016 0 2016 10 2016 5 2016 10 2016 0 2016 5 2016 5 2016 11 2016 0 2016 -11 2016 -11 2016 -5 2016 0 2016 0 2016 -5 2016 -5 2016 -5 2016 0 2016 5 2016 5 2016 5 2016 11 2016 11 2016 16 2016 16 2016 33 2016 22 2016 16 2016 16 2016 16 2016 16 2016 22 2016 22 2016 11 2016 20 2016 22 2016 16 2016 11 2016 22 2016 27 2016 27 2016 33 2016 27 2016 33 2016 27 2016 27 2016 30 2016 27 2016 30 2016 33 2016 27 2016 33 2016 33 2016 33 2016 27 2016 30 2016 33 2016 33 2016 33 2016 27 2016 27 2016 22 2016 27 2016 27 2016 27 2016 22 2016 11 2016 0 2016 5 2016 5 2016 5 2016 5 2016 5 2016 11 2016 16 2016 16 2016 22 2016 27 2016 33 2016 38 2016 33 2016 33 2016 38 2016 38 2016 38 2016 44 2016 38 2016 38 2016 38 2016 44 2016 38 2016 44 2016 44 2016 44 2016 44 2016 38 2016 30 2016 33 2016 33 2016 38 2016 40 2016 40 2016 38 2016 40 2016 38 2016 40 2016 33 2016 33 2016 30 2016 33 2016 38 2016 30 2016 38 2016 38 2016 44 2016 44 2016 44 2016 50 2016 44 2016 44 2016 50 2016 50 2016 44 2016 44 2016 33 2016 33 2016 33 2016 33 2016 -5 2016 -11 2016 -22 2016 -16 2016 -16 2016 -22 2016 -22 2016 -27 2016 -27 2016 -27 2016 -27 2016 -27 2016 -33 2016 -33 2016 -33 2016 -38 2016 -38 2016 -44 2016 -55 2016 -50 2016 -55 2016 -38 2016 -38 2016 -50 2016 -61 2016 -50 2016 -50 2016 -50 2016 -38 2016 -33 2016 -33 2016 -33 2016 -27 2016 -27 2016 -16 2016 -11 2016 -5 2016 0 2016 5 2016 5 2016 11 2016 11 2016 11 2016 5 2016 5 2016 16 2016 0 2016 -11 2016 -5 2016 0 2016 0 2016 5 2016 5 2016 -33 2016 -5 2016 -38 2016 -27 2016 -55 2016 -61 2016 -44 2016 -61 2016 -38 2016 -33 2016 -38 2016 -38 2016 -50 2016 -55 2016 -61 2016 -66 2016 -77 2016 -77 2016 -88 2016 -94 2016 -100 2016 -94 2016 -100 2016 -94 2016 -88 2016 -83 2016 -77 2016 -72 2016 -72 2016 -72 2016 -66 2016 -66 2016 -66 2016 -55 2016 -44 2016 -33 2016 -33 2016 -33 2016 -33 2016 -16 2016 0 2016 11 2016 11 2016 16 2016 16 2016 22 2016 22 2016 27 2016 27 2016 22 2016 27 2016 27 2016 16 2016 16 2016 11 2016 16 2016 16 2016 0 2016 -33 2016 -38 2016 -50 2016 -50 2016 -44 2016 -50 2016 -44 2016 -50 2016 -50 2016 -44 2016 -33 2016 -27 2016 -33 2016 -33 2016 -38 2016 -33 2016 -38 2016 -33 2016 -50 2016 -33 2016 -44 2016 -44 2016 -38 2016 -33 2016 -33 2016 -27 2016 -33 2016 -33 2016 -30 2016 -27 2016 -27 2016 -22 2016 -22 2016 -22 2016 -27 2016 -27 2016 -27 2016 -22 2016 -22 2016 -22 2016 -16 2016 -16 2016 -16 2016 -16 2016 -20 2016 -16 2016 -16 2016 -20 2016 -11 2016 -5 2016 -11 2016 -10 2016 -11 2016 -5 2016 -10 2016 -5 2016 -10 2016 -10 2016 -10 2016 -10 2016 -10 2016 -10 2016 -11 2016 -11 2016 -11 2016 -20 2016 -22 2016 -22 2016 -27 2016 -30 2016 -27 2016 -33 2016 -33 2016 -38 2016 -38 2016 -44 2016 -50 2016 -61 2016 -55 2016 -44 2016 -50 2016 -50 2016 -50 2016 -61 2016 -66 2016 -61 2016 -100 2016 -94 2016 -66 2016 -66 2016 -66 2016 -72 2016 -66 2016 -66 2016 -66 2016 -72 2016 -72 2016 -72 2016 -77 2016 -77 2016 -88 2016 -83 2016 -83 2016 -83 2016 -83 2016 -83 2016 -83 2016 -83 2016 -88 2016 -83 2016 -88 2016 -77 2016 -83 2016 -88 2016 -105 2016 -94 2016 -100 2016 -100 2016 -105 2016 -116 2016 -122 2016 -122 2016 -138 2016 -122 2016 -127 2016 -144 2016 -150 2016 -144 2016 -127 2016 -122 2016 -138 2016 -150 2016 -150 2016 -150 2016 -150 2016 -160 2016 -155 2016 -144 2016 -140 2016 -144 2016 -160 2016 -155 2016 -160 2016 -150 2016 -150 2016 -140 2016 -138 2016 -127 2016 -127 2016 -127 2016 -127 2016 -133 2016 -133 2016 -133 2016 -133 2016 -133 2016 -127 2016 -127 2016 -116 2016 -116 2016 -105 2016 -105 2016 -100 2016 -100 2016 -100 2016 -88 2016 -88 2016 -88 2016 -77 2016 -77 2016 -66 2016 -72 2016 -66 2016 -77 2016 -88 2016 -88 2016 -77 2016 -83 2016 -94 2016 -94 2016 -88 2016 -94 2016 -100 2016 -100 2016 -100 2016 -94 2016 -100 2016 -105 2016 -111 2016 -111 2016 -105 2016 -111 2016 -111 2016 -111 2016 -116 2016 -116 2016 -111 2016 -116 2016 -122 2016 -127 2016 -133 2016 -133 2016 -133 2016 -133 2016 -133 2016 -138 2016 -138 2016 -138 2016 -144 2016 -144 2016 -144 2016 -144 2016 -150 2016 -150 2016 -150

###### Observations :
- The average temp for 2018 is marginally less(for those recs that have a value)

###### 4.2 TMP_Qlty
The code that denotes a quality status of an AIR-TEMPERATURE-OBSERVATION.

- Type = Qualitative
- Missing  = 9999

In [0]:
cleaned_weather_final[['TMP_Qlty']].groupBy("TMP_Qlty").count().show()

#### Section 5.1 - Dew_Degree
- Quantitative
- MIN: -0982 MAX: +0368
- UNITS: Degrees Celsius
- SCALING FACTOR: 10
- 9999 = Missing.

In [0]:
#Let us find out the missing values
cleaned_weather_final.filter(cleaned_weather_final["DEW_Degree"] == 9999).count()

#### Section 5.2 - Dew_Qlty
- MIN: -0982 MAX: +0368
- UNITS: Degrees Celsius
- SCALING FACTOR: 10
- 9999 = Missing.

In [0]:
cleaned_weather_final[['DEW_Qlty']].groupBy("DEW_Qlty").count().show()

#### Section 6 - Analysis of "Atmospheric pressure"

#### Section 6.1 - SLP_Pressure
The air pressure relative to Mean Sea Level (MSL).
- MIN: 08600 
- MAX: 10900
- UNITS: Hectopascals
- SCALING FACTOR: 10
- 99999 = Missing.

In [0]:
# Let;s analyze the missing values
cleaned_weather_final.filter(cleaned_weather_final["SLP_Pressure"] == 99999).count()

In [0]:
cleaned_weather_final[['SLP_Qlty']].groupBy("SLP_Qlty").count().show()

#### Next, Lets drop all the missing values represented by 9's in the dataset.

In [0]:
cleaned_weather_final.columns


Out[40]: ['YEAR',
 'MONTH',
 'DAY_OF_MONTH',
 'HOUR_BLOCK',
 'STATION',
 'DATE',
 'SOURCE',
 'LATITUDE',
 'LONGITUDE',
 'ELEVATION',
 'NAME',
 'REPORT_TYPE',
 'CALL_SIGN',
 'QUALITY_CONTROL',
 'AW1',
 'GA1',
 'GA2',
 'GA3',
 'GA4',
 'GE1',
 'GF1',
 'KA1',
 'KA2',
 'MA1',
 'MD1',
 'MW1',
 'MW2',
 'OC1',
 'OD1',
 'OD2',
 'REM',
 'EQD',
 'AW2',
 'AX4',
 'GD1',
 'AW5',
 'GN1',
 'AJ1',
 'AW3',
 'MK1',
 'KA4',
 'GG3',
 'AN1',
 'RH1',
 'AU5',
 'HL1',
 'OB1',
 'AT8',
 'AW7',
 'AZ1',
 'CH1',
 'RH3',
 'GK1',
 'IB1',
 'AX1',
 'CT1',
 'AK1',
 'CN2',
 'OE1',
 'MW5',
 'AO1',
 'KA3',
 'AA3',
 'CR1',
 'CF2',
 'KB2',
 'GM1',
 'AT5',
 'AY2',
 'MW6',
 'MG1',
 'AH6',
 'AU2',
 'GD2',
 'AW4',
 'MF1',
 'AA1',
 'AH2',
 'AH3',
 'OE3',
 'AT6',
 'AL2',
 'AL3',
 'AX5',
 'IB2',
 'AI3',
 'CV3',
 'WA1',
 'GH1',
 'KF1',
 'CU2',
 'CT3',
 'SA1',
 'AU1',
 'KD2',
 'AI5',
 'GO1',
 'GD3',
 'CG3',
 'AI1',
 'AL1',
 'AW6',
 'MW4',
 'AX6',
 'CV1',
 'ME1',
 'KC2',
 'CN1',
 'UA1',
 'GD5',
 'UG2',
 'AT3',
 'AT4',
 'GJ1',
 'MV1',
 'GA5',
 'CT2',
 'CG2',
 'ED1',
 'AE1',
 'CO1',
 'KE1',
 'KB1',
 'AI4',
 'MW3',
 'KG2',
 'AA2',
 'AX2',
 'AY1',
 'RH2',
 'OE2',
 'CU3',
 'MH1',
 'AM1',
 'AU4',
 'GA6',
 'KG1',
 'AU3',
 'AT7',
 'KD1',
 'GL1',
 'IA1',
 'GG2',
 'OD3',
 'UG1',
 'CB1',
 'AI6',
 'CI1',
 'CV2',
 'AZ2',
 'AD1',
 'AH1',
 'WD1',
 'AA4',
 'KC1',
 'IA2',
 'CF3',
 'AI2',
 'AT1',
 'GD4',
 'AX3',
 'AH4',
 'KB3',
 'CU1',
 'CN4',
 'AT2',
 'CG1',
 'CF1',
 'GG1',
 'MV2',
 'CW1',
 'GG4',
 'AB1',
 'AH5',
 'CN3',
 'country',
 'WND_Angle',
 'WND_Qlty',
 'WND_Obs',
 'WND_Speed',
 'WND_Speed_Qlty',
 'CIG_Height',
 'CIG_Qlty',
 'CIG_Ceiling',
 'CIG_CAVOK',
 'VIS_Dis',
 'VIS_Qlty',
 'VIS_Var',
 'VIS_Var_Qlty',
 'TMP_Degree',
 'TMP_Qlty',
 'DEW_Degree',
 'DEW_Qlty',
 'SLP_Pressure',
 'SLP_Qlty']

In [0]:
#Let's remove missing values for WND_Angle
##df.filter(df["age"]>24).show()
cleaned_weather_final_no_missing_vals = cleaned_weather_final.filter((cleaned_weather_final['WND_Angle'] != 999) | (cleaned_weather_final['WND_Obs'] != '9') | (cleaned_weather_final['WND_Speed'] != 9999) | (cleaned_weather_final['CIG_Height'] != 99999)|(cleaned_weather_final['CIG_CAVOK'] != '9') | (cleaned_weather_final['VIS_Dis'] != 999999)|(cleaned_weather_final['VIS_Var'] != '9') |(cleaned_weather_final['TMP_Degree'] != 9999) | (cleaned_weather_final['DEW_Degree'] != 9999) |(cleaned_weather_final['SLP_Pressure'] != 99999)|(cleaned_weather_final['REPORT_TYPE'] == 'FM-15'))


In [0]:
cleaned_weather_19_final.columns

Out[43]: ['YEAR',
 'MONTH',
 'DAY_OF_MONTH',
 'HOUR_BLOCK',
 'STATION',
 'DATE',
 'SOURCE',
 'LATITUDE',
 'LONGITUDE',
 'ELEVATION',
 'NAME',
 'REPORT_TYPE',
 'CALL_SIGN',
 'QUALITY_CONTROL',
 'AW1',
 'GA1',
 'GA2',
 'GA3',
 'GA4',
 'GE1',
 'GF1',
 'KA1',
 'KA2',
 'MA1',
 'MD1',
 'MW1',
 'MW2',
 'OC1',
 'OD1',
 'OD2',
 'REM',
 'EQD',
 'AW2',
 'AX4',
 'GD1',
 'AW5',
 'GN1',
 'AJ1',
 'AW3',
 'MK1',
 'KA4',
 'GG3',
 'AN1',
 'RH1',
 'AU5',
 'HL1',
 'OB1',
 'AT8',
 'AW7',
 'AZ1',
 'CH1',
 'RH3',
 'GK1',
 'IB1',
 'AX1',
 'CT1',
 'AK1',
 'CN2',
 'OE1',
 'MW5',
 'AO1',
 'KA3',
 'AA3',
 'CR1',
 'CF2',
 'KB2',
 'GM1',
 'AT5',
 'AY2',
 'MW6',
 'MG1',
 'AH6',
 'AU2',
 'GD2',
 'AW4',
 'MF1',
 'AA1',
 'AH2',
 'AH3',
 'OE3',
 'AT6',
 'AL2',
 'AL3',
 'AX5',
 'IB2',
 'AI3',
 'CV3',
 'WA1',
 'GH1',
 'KF1',
 'CU2',
 'CT3',
 'SA1',
 'AU1',
 'KD2',
 'AI5',
 'GO1',
 'GD3',
 'CG3',
 'AI1',
 'AL1',
 'AW6',
 'MW4',
 'AX6',
 'CV1',
 'ME1',
 'KC2',
 'CN1',
 'UA1',
 'GD5',
 'UG2',
 'AT3',
 'AT4',
 'GJ1',
 'MV1',
 'GA5',
 'CT2',
 'CG2',
 'ED1',
 'AE1',
 'CO1',
 'KE1',
 'KB1',
 'AI4',
 'MW3',
 'KG2',
 'AA2',
 'AX2',
 'AY1',
 'RH2',
 'OE2',
 'CU3',
 'MH1',
 'AM1',
 'AU4',
 'GA6',
 'KG1',
 'AU3',
 'AT7',
 'KD1',
 'GL1',
 'IA1',
 'GG2',
 'OD3',
 'UG1',
 'CB1',
 'AI6',
 'CI1',
 'CV2',
 'AZ2',
 'AD1',
 'AH1',
 'WD1',
 'AA4',
 'KC1',
 'IA2',
 'CF3',
 'AI2',
 'AT1',
 'GD4',
 'AX3',
 'AH4',
 'KB3',
 'CU1',
 'CN4',
 'AT2',
 'CG1',
 'CF1',
 'GG1',
 'MV2',
 'CW1',
 'GG4',
 'AB1',
 'AH5',
 'CN3',
 'country',
 'WND_Angle',
 'WND_Qlty',
 'WND_Obs',
 'WND_Speed',
 'WND_Speed_Qlty',
 'CIG_Height',
 'CIG_Qlty',
 'CIG_Ceiling',
 'CIG_CAVOK',
 'VIS_Dis',
 'VIS_Qlty',
 'VIS_Var',
 'VIS_Var_Qlty',
 'TMP_Degree',
 'TMP_Qlty',
 'DEW_Degree',
 'DEW_Qlty',
 'SLP_Pressure',
 'SLP_Qlty']

In [0]:
cleaned_weather_final_no_missing_vals_19 = cleaned_weather_19_final.filter((cleaned_weather_19_final['WND_Angle'] != 999) | (cleaned_weather_19_final['WND_Obs'] != '9') | (cleaned_weather_19_final['WND_Speed'] != 9999) | (cleaned_weather_19_final['CIG_Height'] != 99999)|(cleaned_weather_19_final['CIG_CAVOK'] != '9') | (cleaned_weather_19_final['VIS_Dis'] != 999999)|(cleaned_weather_19_final['VIS_Var'] != '9') |(cleaned_weather_19_final['TMP_Degree'] != 9999) | (cleaned_weather_19_final['DEW_Degree'] != 9999) |(cleaned_weather_19_final['SLP_Pressure'] != 99999)|(cleaned_weather_19_final['REPORT_TYPE'] == 'FM-15'))


In [0]:
cleaned_weather_final_no_missing_vals.count()

In [0]:
cleaned_weather_final_no_missing_vals.count()

Out[46]: 217850990

In [0]:
cleaned_weather_final_no_missing_vals_19.count()

Out[47]: 57593288

In [0]:
weather_final = cleaned_weather_final_no_missing_vals
weather_final_19 = cleaned_weather_final_no_missing_vals_19

In [0]:
#weather_final= cleaned_weather_final_no_missing_vals.drop("CIG_Ceiling")

In [0]:
weather_final= cleaned_weather_final_no_missing_vals.drop("CIG_Ceiling")

In [0]:
weather_final.count()

Out[49]: 217850990

In [0]:
weather_final.write.parquet("dbfs:/mnt/mids-w261/team20SSDK/strategy/weather_all_columns")

In [0]:
weather_final_19.write.parquet("dbfs:/mnt/mids-w261/team20SSDK/strategy/weather_19_all_columns")

In [0]:
missing_vals_train_val = cleaned_weather_final.filter((cleaned_weather_final['WND_Angle'] == 999) | (cleaned_weather_final['WND_Obs'] == '9') | (cleaned_weather_final['WND_Speed'] == 9999) | (cleaned_weather_final['CIG_Height'] == 99999)|(cleaned_weather_final['CIG_CAVOK'] == '9') | (cleaned_weather_final['VIS_Dis'] == 999999)|(cleaned_weather_final['VIS_Var'] == '9') |(cleaned_weather_final['TMP_Degree'] == 9999) | (cleaned_weather_final['DEW_Degree'] == 9999) |(cleaned_weather_final['SLP_Pressure'] == 99999)|(cleaned_weather_final['REPORT_TYPE'] == 'FM-15'))

In [0]:
missing_vals_19 = cleaned_weather_19_final.filter((cleaned_weather_19_final['WND_Angle'] == 999) | (cleaned_weather_19_final['WND_Obs'] == '9') | (cleaned_weather_19_final['WND_Speed'] == 9999) | (cleaned_weather_19_final['CIG_Height'] == 99999)|(cleaned_weather_19_final['CIG_CAVOK'] == '9') | (cleaned_weather_19_final['VIS_Dis'] == 999999)|(cleaned_weather_19_final['VIS_Var'] == '9') |(cleaned_weather_19_final['TMP_Degree'] == 9999) | (cleaned_weather_19_final['DEW_Degree'] == 9999) |(cleaned_weather_19_final['SLP_Pressure'] == 99999)|(cleaned_weather_19_final['REPORT_TYPE'] == 'FM-15'))

In [0]:
missing_vals_train_val[['WND_Angle','WND_Obs','WND_Speed','CIG_Height','VIS_Dis','TMP_Degree','DEW_Degree','SLP_Pressure','YEAR']].display()

WND_Angle WND_Obs WND_Speed CIG_Height VIS_Dis TMP_Degree DEW_Degree SLP_Pressure YEAR 230 N 36 91 999999 0 -10 99999 2016 999 V 26 122 999999 0 -10 99999 2016 220 N 36 183 999999 0 -5 99999 2016 230 N 21 274 999999 10 -10 99999 2016 210 N 15 427 999999 5 -11 99999 2016 999 C 0 610 999999 10 -10 99999 2016 110 N 15 549 999999 0 -5 99999 2016 999 V 15 853 999999 5 -11 99999 2016 999 V 21 945 999999 5 -16 99999 2016 999 C 0 1067 999999 11 -22 99999 2016 90 N 26 1189 999999 0 -33 99999 2016 90 N 31 22000 999999 -11 -38 99999 2016 90 N 36 22000 999999 -11 -44 99999 2016 100 N 41 22000 999999 -5 -38 99999 2016 90 N 46 22000 999999 0 -33 99999 2016 90 N 51 22000 999999 0 -33 99999 2016 90 N 51 22000 999999 -5 -38 99999 2016 100 N 36 22000 999999 -5 -38 99999 2016 110 N 21 1189 999999 -5 -38 99999 2016 999 C 0 22000 999999 0 -44 99999 2016 100 N 36 1311 999999 5 -50 99999 2016 80 N 41 1250 999999 5 -55 99999 2016 90 V 41 3048 999999 5 -61 99999 2016 80 N 51 2438 999999 11 -66 99999 2016 70 N 51 22000 999999 11 -61 99999 2016 80 N 57 3353 999999 16 -66 99999 2016 60 N 41 22000 999999 16 -66 99999 2016 30 N 62 1189 999999 33 -66 99999 2016 90 N 31 3048 999999 22 -61 99999 2016 80 V 41 2591 999999 16 -55 99999 2016 70 N 77 3353 999999 16 -55 99999 2016 110 N 36 3353 999999 16 -55 99999 2016 80 N 57 22000 999999 16 -55 99999 2016 80 N 57 1036 999999 22 -50 99999 2016 20 N 26 1433 999999 22 -50 99999 2016 60 N 36 1463 999999 11 -50 99999 2016 50 N 46 792 999999 20 -50 99999 2016 60 V 46 792 999999 22 -44 99999 2016 70 N 36 1372 999999 16 -38 99999 2016 80 N 31 1280 999999 11 -22 99999 2016 100 N 41 1128 999999 22 -22 99999 2016 100 N 46 1128 999999 27 -27 99999 2016 90 N 31 1067 999999 27 -27 99999 2016 90 N 36 1097 999999 33 -27 99999 2016 100 N 41 1219 999999 27 -27 99999 2016 110 N 46 22000 999999 33 -27 99999 2016 90 N 57 914 999999 27 -16 99999 2016 100 N 62 914 999999 27 -11 99999 2016 100 N 51 853 999999 30 -10 99999 2016 100 N 46 792 999999 27 -11 99999 2016 100 N 57 3658 999999 30 -10 99999 2016 90 N 67 3353 999999 33 -11 99999 2016 110 N 36 3048 999999 27 -5 99999 2016 100 N 51 22000 999999 33 0 99999 2016 100 N 62 22000 999999 33 -5 99999 2016 110 N 62 2286 999999 33 -5 99999 2016 150 V 41 792 999999 27 0 99999 2016 999 V 31 640 999999 30 0 99999 2016 150 N 21 701 999999 33 0 99999 2016 160 V 41 1128 999999 33 -11 99999 2016 160 N 36 1189 999999 33 -5 99999 2016 190 V 46 640 999999 27 0 99999 2016 180 N 46 945 999999 27 0 99999 2016 130 N 31 1128 999999 22 0 99999 2016 160 N 26 1067 999999 27 -5 99999 2016 150 N 26 1067 999999 27 -5 99999 2016 999 V 26 1250 999999 27 -5 99999 2016 150 N 26 22000 999999 22 -16 99999 2016 110 N 26 22000 999999 11 -22 99999 2016 999 V 21 1524 999999 0 -22 99999 2016 90 N 36 22000 999999 5 -22 99999 2016 90 N 31 22000 999999 5 -27 99999 2016 100 N 36 22000 999999 5 -27 99999 2016 90 N 31 22000 999999 5 -27 99999 2016 80 N 31 22000 999999 5 -27 99999 2016 80 N 41 22000 999999 11 -27 99999 2016 90 N 36 22000 999999 16 -27 99999 2016 90 N 31 732 999999 16 -27 99999 2016 90 N 36 1219 999999 22 -16 99999 2016 100 N 46 2743 999999 27 -11 99999 2016 100 N 62 2743 999999 33 -5 99999 2016 100 N 57 1158 999999 38 -5 99999 2016 100 N 88 1189 999999 33 -5 99999 2016 100 N 57 22000 999999 33 -5 99999 2016 100 N 67 22000 999999 38 -11 99999 2016 100 N 62 2896 999999 38 -16 99999 2016 110 N 62 22000 999999 38 -22 99999 2016 100 N 57 22000 999999 44 -27 99999 2016 100 N 36 22000 999999 38 -33 99999 2016 100 N 41 22000 999999 38 -38 99999 2016 100 N 46 22000 999999 38 -44 99999 2016 110 N 46 22000 999999 44 -44 99999 2016 110 N 62 3353 999999 38 -16 99999 2016 100 N 46 22000 999999 44 -27 99999 2016 100 N 46 22000 999999 44 -27 99999 2016 100 N 57 2896 999999 44 -22 99999 2016 110 N 57 3658 999999 44 -22 99999 2016 100 N 57 823 999999 38 -11 99999 2016 100 N 77 3658 999999 30 0 99999 2016 100 N 67 3353 999999 33 -5 99999 2016 100 N 51 22000 999999 33 -11 99999 2016 90 N 51 945 999999 38 -11 99999 2016 100 N 82 701 

###### Observations:
- Intersting to note that 2018 has only missing values in WND_SPEED and SLP_Pressure

In [0]:
missing_vals_19[['WND_Angle','WND_Obs','WND_Speed','CIG_Height','VIS_Dis','TMP_Degree','DEW_Degree','SLP_Pressure','YEAR']].display()

WND_Angle WND_Obs WND_Speed CIG_Height VIS_Dis TMP_Degree DEW_Degree SLP_Pressure YEAR 999 R 27 99999 999999 -152 9999 99999 2019 999 9 9999 99999 999999 -153 9999 99999 2019 999 9 9999 99999 999999 -153 9999 99999 2019 999 9 9999 99999 999999 -154 9999 99999 2019 999 9 9999 99999 999999 -154 9999 99999 2019 999 9 9999 99999 999999 -155 9999 99999 2019 999 9 9999 99999 999999 -155 9999 99999 2019 999 9 9999 99999 999999 -156 9999 99999 2019 999 9 9999 99999 999999 -157 9999 99999 2019 999 9 9999 99999 999999 -158 9999 99999 2019 999 9 9999 99999 999999 -158 9999 99999 2019 999 9 9999 99999 999999 -158 9999 99999 2019 999 R 23 99999 999999 -159 9999 99999 2019 999 9 9999 99999 999999 -160 9999 99999 2019 999 9 9999 99999 999999 -159 9999 99999 2019 999 9 9999 99999 999999 -158 9999 99999 2019 999 9 9999 99999 999999 -157 9999 99999 2019 999 9 9999 99999 999999 -158 9999 99999 2019 999 9 9999 99999 999999 -160 9999 99999 2019 999 9 9999 99999 999999 -161 9999 99999 2019 999 9 9999 99999 999999 -162 9999 99999 2019 999 9 9999 99999 999999 -164 9999 99999 2019 999 9 9999 99999 999999 -165 9999 99999 2019 999 9 9999 99999 999999 -166 9999 99999 2019 999 R 14 99999 999999 -166 9999 99999 2019 999 9 9999 99999 999999 -166 9999 99999 2019 999 9 9999 99999 999999 -167 9999 99999 2019 999 9 9999 99999 999999 -167 9999 99999 2019 999 9 9999 99999 999999 -167 9999 99999 2019 999 9 9999 99999 999999 -167 9999 99999 2019 999 9 9999 99999 999999 -167 9999 99999 2019 999 9 9999 99999 999999 -168 9999 99999 2019 999 9 9999 99999 999999 -168 9999 99999 2019 999 9 9999 99999 999999 -168 9999 99999 2019 999 9 9999 99999 999999 -169 9999 99999 2019 999 9 9999 99999 999999 -168 9999 99999 2019 999 R 4 99999 999999 -169 9999 99999 2019 999 9 9999 99999 999999 -173 9999 99999 2019 999 9 9999 99999 999999 -175 9999 99999 2019 999 9 9999 99999 999999 -180 9999 99999 2019 999 9 9999 99999 999999 -180 9999 99999 2019 999 9 9999 99999 999999 -177 9999 99999 2019 999 9 9999 99999 999999 -181 9999 99999 2019 999 9 9999 99999 999999 -179 9999 99999 2019 999 9 9999 99999 999999 -175 9999 99999 2019 999 9 9999 99999 999999 -176 9999 99999 2019 999 9 9999 99999 999999 -184 9999 99999 2019 999 9 9999 99999 999999 -177 9999 99999 2019 999 R 3 99999 999999 -173 9999 99999 2019 999 9 9999 99999 999999 -186 9999 99999 2019 999 9 9999 99999 999999 -181 9999 99999 2019 999 9 9999 99999 999999 -181 9999 99999 2019 999 9 9999 99999 999999 -184 9999 99999 2019 999 9 9999 99999 999999 -184 9999 99999 2019 999 9 9999 99999 999999 -184 9999 99999 2019 999 9 9999 99999 999999 -183 9999 99999 2019 999 9 9999 99999 999999 -181 9999 99999 2019 999 9 9999 99999 999999 -179 9999 99999 2019 999 9 9999 99999 999999 -189 9999 99999 2019 999 9 9999 99999 999999 -195 9999 99999 2019 999 R 4 99999 999999 -195 9999 99999 2019 999 9 9999 99999 999999 -189 9999 99999 2019 999 9 9999 99999 999999 -185 9999 99999 2019 999 9 9999 99999 999999 -189 9999 99999 2019 999 9 9999 99999 999999 -187 9999 99999 2019 999 9 9999 99999 999999 -185 9999 99999 2019 999 9 9999 99999 999999 -192 9999 99999 2019 999 9 9999 99999 999999 -191 9999 99999 2019 999 9 9999 99999 999999 -192 9999 99999 2019 999 9 9999 99999 999999 -188 9999 99999 2019 999 9 9999 99999 999999 -189 9999 99999 2019 999 9 9999 99999 999999 -194 9999 99999 2019 999 R 1 99999 999999 -194 9999 99999 2019 999 9 9999 99999 999999 -193 9999 99999 2019 999 9 9999 99999 999999 -199 9999 99999 2019 999 9 9999 99999 999999 -197 9999 99999 2019 999 9 9999 99999 999999 -196 9999 99999 2019 999 9 9999 99999 999999 -197 9999 99999 2019 999 9 9999 99999 999999 -204 9999 99999 2019 999 9 9999 99999 999999 -200 9999 99999 2019 999 9 9999 99999 999999 -200 9999 99999 2019 999 9 9999 99999 999999 -205 9999 99999 2019 999 9 9999 99999 999999 -205 9999 99999 2019 999 9 9999 99999 999999 -205 9999 99999 2019 999 9 9999 99999 999999 9999 9999 99999 2019 999 9 9999 99999 999999 9999 9999 99999 2019 999 R 2 99999 999999 -203 9999 99999 2019 999 9 9999 99999 99

In [0]:
display(dbutils.fs.ls("dbfs:/mnt/mids-w261/team20SSDK/"))